# BITCOIN BOT PROJECT
The goal of this project is to develop a working trading bot with the binance api. The signaller is supertrend on the 1m timescale.

## Project Plan
#### PHASE 1 - DATA COLLECTION AND BACKTESTS
1. Data Collection
2. Data Clean
3. Build Supertrend Signal
4. Carry out back test
5. Tune back test hyperparameters
6. Investigate optimisation
7. Retune hyperparameters
8. Evaluate the strategy - Bot / no bot

#### PHASE 2 - BUILD AND TEST BOT IN LOCAL ENV
1. Review binance bot options and develop bot type / operation and functionality
2. Build bot
3. Test strategy offline
4. Debug and optimise
5. Add new data to initial phase 1 backtest to see if results are comparable and hyperparameters similar or unchanged
6. Debug / optimise / retest in local env


#### PHASE 3 - LIVE TESTS
1. Commence live tests with small initial capital and low risk
2. Add new data to initial phase 1 backtest to see if results are comparable and hyperparameters similar or unchanged
3. Debug / optimise / retest in live environment

#### PHASE 4 - RUN BOT
1. RUN BOT WITH FULLY OPTIMISED STRATEGY / HYPERPARAMETERS / RISK 
2. COLLECT GAINS

In [519]:
# Import libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os
import datetime
import time
import warnings
import math

from tqdm import tqdm
from collections import Counter

pd.set_option("display.max_columns", None)

warnings.filterwarnings("ignore")

## PHASE 1

In [762]:
os.listdir()

['HP_Summary.png',
 'HPrev1_Summary.png',
 'data050322.csv',
 'data.csv',
 'csv_build.ipynb',
 'COINBASE_BTCUSD, 1.csv',
 'BTC_BOT_1.ipynb',
 'COINBASE_BTCUSD, 1A.csv',
 '1m0703tv.csv',
 'BTC_BOT_3.ipynb',
 '.ipynb_checkpoints',
 'BTC_BOT_2.ipynb',
 'supertrend.csv']

In [764]:
# Import base data
df = pd.read_csv("1m0703tv.csv")

In [765]:
print(df.shape)
df.tail()

(15342, 39)


time      open      high       low     close  Developing Poc  \
15337  1649345820  43196.57  43256.36  43196.47  43251.70             NaN   
15338  1649345880  43251.70  43251.70  43207.68  43212.91             NaN   
15339  1649345940  43212.63  43287.22  43208.78  43258.00             NaN   
15340  1649346000  43259.90  43277.07  43231.29  43268.83             NaN   
15341  1649346060  43268.83  43289.00  43258.01  43266.62             NaN   

       Developing VA High  Developing VA Low       Plot  Up Trend  \
15337                 NaN                NaN  43224.135       NaN   
15338                 NaN                NaN  43232.305       NaN   
15339                 NaN                NaN  43235.315       NaN   
15340                 NaN                NaN  43264.365       NaN   
15341                 NaN                NaN  43268.565       NaN   

         Down Trend  VWAP  Upper Band  Lower Band        Plot.1        Plot.2  \
15337  43285.211337   NaN         NaN         NaN  43214.782429  43234.118798   
15338  43285.211337   NaN         NaN         NaN  43214.604103  43232.487352   
15339  43285.211337   NaN         NaN         NaN  43218.737045  43234.449863   
15340  43285.211337   NaN         NaN         NaN  43223.507803  43237.094489   
15341  43285.211337   NaN         NaN         NaN  43227.773727  43239.494913   

             Plot.3        Plot.4        Plot.5        Plot.6        Plot.7  \
15337  43251.920635  43268.179611  43283.017631  43296.580227  43309.010169   
15338  43249.403820  43265.109077  43279.597746  43292.942391  43305.241535   
15339  43249.958412  43264.714129  43278.544198  43291.423157  43303.388926   
15340  43251.175934  43264.942788  43278.070334  43290.440845  43302.033674   
15341  43252.280712  43265.129300  43277.593733  43289.478200  43300.710785   

             Plot.8     Volume  Volume MA       Basis         Upper  \
15337  43463.137492  11.933339  15.960710  43228.6460  43419.657627   
15338  43460.647667  10.424470  15.976423  43223.7115  43410.958117   
15339  43458.631272  11.998091  16.069669  43220.8095  43403.997489   
15340  43456.742702  10.091988  15.929854  43218.1055  43396.724883   
15341  43454.867650   5.785701  15.466588  43215.4475  43389.355784   

              Lower        MA2       MA10        MA20        MA50        MA55  \
15337  43037.634373  43223.780  43146.523  43228.6460  43333.8294  43445.4651   
15338  43036.464883  43232.305  43143.194  43223.7115  43329.2696  43440.9707   
15339  43037.621511  43235.455  43152.632  43220.8095  43326.0006  43436.9164   
15340  43039.486117  43263.415  43163.327  43218.1055  43323.0774  43432.4060   
15341  43041.539216  43268.565  43182.304  43215.4475  43319.6186  43427.6211   

             MA200        RSI  Histogram       MACD     Signal          K  \
15337  43514.65660  51.070777   6.203471 -54.923566 -61.127037  78.975853   
15338  43511.65485  47.249125  10.133805 -48.459780 -58.593585  90.392087   
15339  43508.85485  51.767322  15.477757 -39.246390 -54.724146  95.031053   
15340  43506.03755  52.812747  19.205927 -30.716737 -49.922664  95.031053   
15341  43503.23190  52.752488  20.957178 -23.726192 -44.683370  99.926635   

               D  
15337  53.108808  
15338  74.630136  
15339  88.132997  
15340  93.484731  
15341  96.662914

In [766]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15342 entries, 0 to 15341
Data columns (total 39 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   time                15342 non-null  int64  
 1   open                15342 non-null  float64
 2   high                15342 non-null  float64
 3   low                 15342 non-null  float64
 4   close               15342 non-null  float64
 5   Developing Poc      0 non-null      float64
 6   Developing VA High  0 non-null      float64
 7   Developing VA Low   0 non-null      float64
 8   Plot                15342 non-null  float64
 9   Up Trend            7835 non-null   float64
 10  Down Trend          7499 non-null   float64
 11  VWAP                0 non-null      float64
 12  Upper Band          0 non-null      float64
 13  Lower Band          0 non-null      float64
 14  Plot.1              15323 non-null  float64
 15  Plot.2              15318 non-null  float64
 16  Plot

In [767]:
# Let's get our time feature to show the proper time
df.time = pd.to_datetime(df["time"], unit="s")

In [721]:
# df.head(5)

In [768]:
# For now let's isolate our supertrend and price features
df_super = df[["time", "open", "high", "low", "close", "Up Trend", "Down Trend"]]
df_super.rename(columns={"Up Trend": "uptrend", "Down Trend": "downtrend"}, inplace=True)
df_super.head(2)
# Ok looking cleaner already!

time      open      high       low     close  uptrend  \
0 2022-03-28 00:00:00  46850.01  46852.16  46801.91  46819.78      NaN   
1 2022-03-28 00:01:00  46819.79  46844.21  46800.77  46839.97      NaN   

   downtrend  
0        0.0  
1        NaN

In [769]:
# Show a sample of data points
df_super.loc[10:15]

time      open      high       low     close  uptrend  \
10 2022-03-28 00:10:00  46764.48  46764.48  46734.57  46749.06      NaN   
11 2022-03-28 00:11:00  46749.06  46799.14  46745.00  46787.03      NaN   
12 2022-03-28 00:12:00  46798.75  46799.14  46745.95  46766.77      NaN   
13 2022-03-28 00:13:00  46769.17  46770.37  46741.30  46741.30      NaN   
14 2022-03-28 00:14:00  46741.30  46745.82  46723.94  46734.46      NaN   
15 2022-03-28 00:15:00  46734.38  46745.82  46692.21  46701.12      NaN   

       downtrend  
10  46914.822600  
11  46914.822600  
12  46914.822600  
13  46912.575270  
14  46882.510243  
15  46867.965219

In [770]:
# Let's check that our data is accurate and that where uptrend==NAN; downtrend==float and vice versa
df_super[df_super.uptrend.isna()].isna().sum()
# Ok

time            0
open            0
high            0
low             0
close           0
uptrend      7507
downtrend       8
dtype: int64

#### NARRATIVE
1. We have 19745 data points which equates to 19745 minutes, ~13 days or ~2 weeks worth of data
2. Our period of interest is between mid to late March 2022. This may be of interest when we need to optimise.

#### PLAN - we need to build some features to help our backtest, some possible features
1. We need to build a signal feature that states buy or sell signal. Buy flashes when price closes above down trend, sell flashes when price closes below up trend.
2. A feature that holds the current profit / loss in a signal (same for percent gain / loss)
3. A feature that holds the max profit in a signal period (same for max percent gain)
4. A feature that holds the max drawdown in a signal period (same for max percent loss)

5. We'll then create a trade dataset that lists out only the key information for each trade



In [771]:
# Buy / Sell signal feature 
# If uptrend>0 then buy, elif downtrend>0 then sell, else: NAN

def signal(row):
    """
    In this function we'll build the feature that states whether we're in a buy or sell signal
    """
    
    uptrend = row[5]
    downtrend = row[6]


    if uptrend>0:
        return "buy"
    elif downtrend>0:
        return "sell"
    else:
        return "no_signal"
    

In [772]:
signal_ = df_super.apply(signal, axis='columns').to_frame()

In [773]:
df_super = df_super.join(signal_)
df_super.rename(columns={0: 'signal'}, inplace=True)

In [774]:
# Check the signals
df_super[110:120]
# Looking good

time      open      high       low     close  uptrend  \
110 2022-03-28 01:50:00  46821.98  46830.00  46816.66  46829.08      NaN   
111 2022-03-28 01:51:00  46829.05  46863.34  46825.95  46835.58      NaN   
112 2022-03-28 01:52:00  46832.54  46852.70  46830.97  46841.60      NaN   
113 2022-03-28 01:53:00  46841.66  46857.70  46833.02  46855.30      NaN   
114 2022-03-28 01:54:00  46859.03  46863.79  46832.88  46837.32      NaN   
115 2022-03-28 01:55:00  46836.53  46856.09  46827.95  46848.57      NaN   
116 2022-03-28 01:56:00  46848.57  46849.34  46792.01  46796.74      NaN   
117 2022-03-28 01:57:00  46796.55  46822.12  46793.61  46822.05      NaN   
118 2022-03-28 01:58:00  46822.11  46840.00  46813.33  46840.00      NaN   
119 2022-03-28 01:59:00  46839.86  46843.27  46818.89  46821.78      NaN   

        downtrend signal  
110  46867.910736   sell  
111  46867.910736   sell  
112  46867.910736   sell  
113  46867.910736   sell  
114  46867.910736   sell  
115  46867.910736   sell  
116  46867.910736   sell  
117  46867.910736   sell  
118  46867.910736   sell  
119  46867.910736   sell

In [775]:
df_super.head(2)

time      open      high       low     close  uptrend  \
0 2022-03-28 00:00:00  46850.01  46852.16  46801.91  46819.78      NaN   
1 2022-03-28 00:01:00  46819.79  46844.21  46800.77  46839.97      NaN   

   downtrend     signal  
0        0.0  no_signal  
1        NaN  no_signal

In [776]:
df_super.loc[0].close

46819.78

#### Signal Trigger Feature
We need a feature that identifies each row where a trade signal is triggered

In [777]:
idx = 0
def trigger(row):
    global idx
    
    signal = row[7]
    
    if idx == 0:
        idx+=1
        return np.nan
    
    elif signal=="sell" and df_super.loc[idx-1].signal!="sell":
        idx+=1
        return "sellsig"

    elif signal=="buy" and df_super.loc[idx-1].signal!="buy":
        idx+=1
        return "buysig"
    
    else:
        idx+=1
        return "nosig"

In [778]:
trigger = df_super.apply(trigger, axis="columns").to_frame()

In [779]:
df_super = df_super.join(trigger)
df_super.rename(columns={0: 'trigger'}, inplace=True)

In [780]:
df_super[(df_super.trigger=="sellsig") | (df_super.trigger=="buysig")].iloc[71:79]

time      open      high       low     close  \
2699 2022-03-29 20:59:00  47449.96  47503.58  47449.96  47496.62   
2712 2022-03-29 21:12:00  47406.95  47408.83  47282.58  47313.65   
2732 2022-03-29 21:32:00  47481.12  47499.76  47477.44  47499.76   
2739 2022-03-29 21:39:00  47456.45  47456.45  47430.84  47432.26   
2798 2022-03-29 22:38:00  47231.63  47340.47  47215.91  47323.45   
2880 2022-03-30 00:00:00  47448.41  47451.41  47401.00  47430.74   
2931 2022-03-30 00:51:00  47182.32  47246.00  47180.41  47241.74   
2942 2022-03-30 01:02:00  47246.10  47249.62  47162.97  47171.06   

           uptrend     downtrend signal  trigger  
2699  47356.350123           NaN    buy   buysig  
2712           NaN  47492.498634   sell  sellsig  
2732  47410.412801           NaN    buy   buysig  
2739           NaN  47514.605464   sell  sellsig  
2798  47032.826200           NaN    buy   buysig  
2880           NaN  47526.938709   sell  sellsig  
2931  47101.368436           NaN    buy   buysig  
2942           NaN  47345.873351   sell  sellsig

In [781]:
# Now build the current profit feature
idx = 0
# Store the signal trigger index
trig_ind = 0
def status(row):
    """
    This function returns the current price difference from signal trigger to close price at the
    data point timestamp
    """
    
    global idx
    global trig_ind
    
    close = row[4]
    uptrend = row[5]
    downtrend = row[6]
    signal = row[7]
    
    
    
    # Idx 0 is a non signal so we can return NAN profits
    if idx==0:
        idx+=1
        return np.nan
    
    ### SELLS ###
    # Hunt for signal triggers and set the trigger index
    if signal=="sell" and df_super.signal.loc[idx-1]!="sell":
        # Set the trigger index to the index where signal generated
        trig_ind = idx
        # We have just entered on the close of this candle so our p/l is 0
        idx+=1
        return 0
        # Calculate and return the sell trade position as it progresses
    elif signal=="sell":    
        # Sell profit is close of our trigger candle minus now candle close
        current_pl = df_super.loc[trig_ind].close - close
        idx+=1
        return current_pl
    
    
    ### BUYS ###
    elif signal=="buy" and df_super.signal.loc[idx-1]!="buy":
        trig_ind=idx
        idx+=1
        return 0
        # Calculate and return the buy trade position as it progresses
    elif signal=="buy":
        current_pl = close-df_super.loc[trig_ind].close
        idx+=1
        return current_pl
    
    else:
        idx+=1
        return np.nan

In [782]:
close_pl = df_super.apply(status, axis='columns').to_frame()

In [783]:
# df_super.drop("close_pl", axis=1, inplace=True)

In [784]:
df_super = df_super.join(close_pl)
df_super.rename(columns={0: 'close_pl'}, inplace=True)

In [785]:
df_super.head(3)

time      open      high       low     close  uptrend  \
0 2022-03-28 00:00:00  46850.01  46852.16  46801.91  46819.78      NaN   
1 2022-03-28 00:01:00  46819.79  46844.21  46800.77  46839.97      NaN   
2 2022-03-28 00:02:00  46833.77  46910.00  46833.77  46909.48      NaN   

   downtrend     signal trigger  close_pl  
0        0.0  no_signal     NaN       NaN  
1        NaN  no_signal   nosig       NaN  
2        NaN  no_signal   nosig       NaN

#### NARRATIVE
We've built a buy / sell trade signaller and the closing profit of each candle in a given trade. Now we want to build features that return:
1. the max $-profit in a given trade signal, 
2. the max %-profit in a given trade signal 
3. the stop loss value of a trade signal

In [786]:
idx=0
trig_ind=0
def max_dollar(row):
    """
    in this function we'll calculate the max dollar profit for for each trade candle
    
    """
    
    global idx
    global trig_ind
    
    high = row[2]
    low = row[3]
    close = row[4]
    uptrend = row[5]
    downtrend = row[6]
    signal = row[7]
    
    # Idx 0 is a non signal so we can return NAN profits
    if idx==0:
        idx+=1
        return np.nan
    
    ### SELLS ###
    # Hunt for signal triggers and set the trigger index
    if signal=="sell" and df_super.signal.loc[idx-1]!="sell":
        # Set the trigger index to the index where signal generated
        trig_ind = idx
        # We have just entered on the close of this candle so our p/l is 0
        idx+=1
        return 0
        # Calculate and return the sell trade position as it progresses
    elif signal=="sell":    
        # Sell profit is close of our trigger candle minus now candle close
        current_pl = df_super.loc[trig_ind].close - low
        idx+=1
        return current_pl
    
    
    ### BUYS ###
    elif signal=="buy" and df_super.signal.loc[idx-1]!="buy":
        trig_ind=idx
        idx+=1
        return 0
        # Calculate and return the buy trade position as it progresses
    elif signal=="buy":
        current_pl = high-df_super.loc[trig_ind].close
        idx+=1
        return current_pl
    
    else:
        idx+=1
        return np.nan
    
    
    

In [787]:
max_pl = df_super.apply(max_dollar, axis='columns').to_frame()

df_super = df_super.join(max_pl)
df_super.rename(columns={0: 'max_pl'}, inplace=True)

In [788]:
df_super.max_pl.describe()

count    15333.000000
mean       121.753569
std        200.915841
min       -249.590000
25%          7.540000
50%         59.850000
75%        156.970000
max       1380.490000
Name: max_pl, dtype: float64

In [789]:
df_super.head(1)

time      open      high       low     close  uptrend  downtrend  \
0 2022-03-28  46850.01  46852.16  46801.91  46819.78      NaN        0.0   

      signal trigger  close_pl  max_pl  
0  no_signal     NaN       NaN     NaN

In [790]:
idx=0
trig_ind=0
def max_percent(row):
    """
    in this function we'll calculate the percentage gain loss for each candle in a trade period
    
    """
    
    global idx
    global trig_ind
    
    high = row[2]
    low = row[3]
    close = row[4]
    uptrend = row[5]
    downtrend = row[6]
    signal = row[7]
    max_pl = row[10]
    
    # Idx 0 is a non signal so we can return NAN profits
    if idx==0:
        idx+=1
        return np.nan
    
    ### SELLS ###
    # Hunt for signal triggers and set the trigger index
    if signal=="sell" and df_super.signal.loc[idx-1]!="sell":
        # Set the trigger index to the index where signal generated
        trig_ind = idx
        # We have just entered on the close of this candle so our p/l is 0
        idx+=1
        return 0
        # Calculate and return the sell trade position as it progresses
    elif signal=="sell":    
        # OUr percentage profit is calculated by dividing the gain/loss by the entry price
        pct_profit = round(((max_pl / df_super.loc[trig_ind].close)*100),3)
        idx+=1
        return pct_profit
    
    
    ### BUYS ###
    elif signal=="buy" and df_super.signal.loc[idx-1]!="buy":
        trig_ind=idx
        idx+=1
        return 0
        # Calculate and return the buy trade position as it progresses
    elif signal=="buy":
        # Percentage profit is calculated by dividing the gain/loss by the entry price
        pct_profit = round(((max_pl / df_super.loc[trig_ind].close)*100),3)
        idx+=1
        return pct_profit
    
    else:
        idx+=1
        return np.nan
    
    
    

In [791]:
max_pct = df_super.apply(max_percent, axis='columns').to_frame()

df_super = df_super.join(max_pct)
df_super.rename(columns={0: 'max_pct'}, inplace=True)

#### ADD A MAX DRAWDOWN AND DRAWDOWN PERCENT FEATURES

In [792]:
df_super.tail()

time      open      high       low     close  uptrend  \
15337 2022-04-07 15:37:00  43196.57  43256.36  43196.47  43251.70      NaN   
15338 2022-04-07 15:38:00  43251.70  43251.70  43207.68  43212.91      NaN   
15339 2022-04-07 15:39:00  43212.63  43287.22  43208.78  43258.00      NaN   
15340 2022-04-07 15:40:00  43259.90  43277.07  43231.29  43268.83      NaN   
15341 2022-04-07 15:41:00  43268.83  43289.00  43258.01  43266.62      NaN   

          downtrend signal trigger  close_pl  max_pl  max_pct  
15337  43285.211337   sell   nosig     19.20   74.43    0.172  
15338  43285.211337   sell   nosig     57.99   63.22    0.146  
15339  43285.211337   sell   nosig     12.90   62.12    0.144  
15340  43285.211337   sell   nosig      2.07   39.61    0.092  
15341  43285.211337   sell   nosig      4.28   12.89    0.030

In [793]:
idx=0
trig_ind=0
def max_dd(row):
    """
    in this function we'll calculate the max drawdown for for each trade candle
    
    """
    
    global idx
    global trig_ind
    
    high = row[2]
    low = row[3]
    close = row[4]
    uptrend = row[5]
    downtrend = row[6]
    signal = row[7]
    
    # Idx 0 is a non signal so we can return NAN profits
    if idx==0:
        idx+=1
        return np.nan
    
    ### SELLS ###
    # Hunt for signal triggers and set the trigger index
    if signal=="sell" and df_super.signal.loc[idx-1]!="sell":
        # Set the trigger index to the index where signal generated
        trig_ind = idx
        # We have just entered on the close of this candle so our p/l is 0
        idx+=1
        return 0
        # Calculate and return the sell trade position as it progresses
    elif signal=="sell":    
        # Sell profit is close of our trigger candle minus now candle close
        current_dd = df_super.loc[trig_ind].close - high
        idx+=1
        return current_dd
    
    
    ### BUYS ###
    elif signal=="buy" and df_super.signal.loc[idx-1]!="buy":
        trig_ind=idx
        idx+=1
        return 0
        # Calculate and return the buy trade position as it progresses
    elif signal=="buy":
        current_dd = low-df_super.loc[trig_ind].close
        idx+=1
        return current_dd
    
    else:
        idx+=1
        return np.nan

In [794]:
max_dd = df_super.apply(max_dd, axis='columns').to_frame()

df_super = df_super.join(max_dd)
df_super.rename(columns={0: 'max_dd'}, inplace=True)

In [795]:
df_super.loc[8:16]

time      open      high       low     close  uptrend  \
8  2022-03-28 00:08:00  46747.22  46772.82  46705.33  46731.40      NaN   
9  2022-03-28 00:09:00  46737.52  46764.61  46722.96  46754.96      NaN   
10 2022-03-28 00:10:00  46764.48  46764.48  46734.57  46749.06      NaN   
11 2022-03-28 00:11:00  46749.06  46799.14  46745.00  46787.03      NaN   
12 2022-03-28 00:12:00  46798.75  46799.14  46745.95  46766.77      NaN   
13 2022-03-28 00:13:00  46769.17  46770.37  46741.30  46741.30      NaN   
14 2022-03-28 00:14:00  46741.30  46745.82  46723.94  46734.46      NaN   
15 2022-03-28 00:15:00  46734.38  46745.82  46692.21  46701.12      NaN   
16 2022-03-28 00:16:00  46701.01  46726.42  46669.25  46673.84      NaN   

       downtrend     signal  trigger  close_pl  max_pl  max_pct  max_dd  
8            NaN  no_signal    nosig       NaN     NaN      NaN     NaN  
9   46917.479000       sell  sellsig      0.00    0.00    0.000    0.00  
10  46914.822600       sell    nosig      5.90   20.39    0.044   -9.52  
11  46914.822600       sell    nosig    -32.07    9.96    0.021  -44.18  
12  46914.822600       sell    nosig    -11.81    9.01    0.019  -44.18  
13  46912.575270       sell    nosig     13.66   13.66    0.029  -15.41  
14  46882.510243       sell    nosig     20.50   31.02    0.066    9.14  
15  46867.965219       sell    nosig     53.84   62.75    0.134    9.14  
16  46849.041197       sell    nosig     81.12   85.71    0.183   28.54

#### drawdown percent

In [796]:
idx=0
trig_ind=0
def max_dd_pct(row):
    """
    in this function we'll calculate the percentage gain loss for each candle in a trade period
    
    """
    
    global idx
    global trig_ind
    
    high = row[2]
    low = row[3]
    close = row[4]
    uptrend = row[5]
    downtrend = row[6]
    signal = row[7]
    max_dd = row[12]
    
    # Idx 0 is a non signal so we can return NAN profits
    if idx==0:
        idx+=1
        return np.nan
    
    ### SELLS ###
    # Hunt for signal triggers and set the trigger index
    if signal=="sell" and df_super.signal.loc[idx-1]!="sell":
        # Set the trigger index to the index where signal generated
        trig_ind = idx
        # We have just entered on the close of this candle so our p/l is 0
        idx+=1
        return 0
        # Calculate and return the sell trade position as it progresses
    elif signal=="sell":    
        # OUr percentage profit is calculated by dividing the gain/loss by the entry price
        pct_profit = round(((max_dd / df_super.loc[trig_ind].close)*100),3)
        idx+=1
        return pct_profit
    
    
    ### BUYS ###
    elif signal=="buy" and df_super.signal.loc[idx-1]!="buy":
        trig_ind=idx
        idx+=1
        return 0
        # Calculate and return the buy trade position as it progresses
    elif signal=="buy":
        # Percentage profit is calculated by dividing the gain/loss by the entry price
        pct_profit = round(((max_dd / df_super.loc[trig_ind].close)*100),3)
        idx+=1
        return pct_profit
    
    else:
        idx+=1
        return np.nan
    
    

In [797]:
max_draw_pct = df_super.apply(max_dd_pct, axis='columns').to_frame()

df_super = df_super.join(max_draw_pct)
df_super.rename(columns={0: 'max_dd_pct'}, inplace=True)

In [760]:
df_super

time      open      high       low     close  \
0     2022-03-14 00:00:00  37793.40  37797.17  37763.47  37780.14   
1     2022-03-14 00:01:00  37780.13  37806.22  37757.05  37806.22   
2     2022-03-14 00:02:00  37811.02  37819.97  37794.89  37816.18   
3     2022-03-14 00:03:00  37816.18  37818.51  37756.99  37797.80   
4     2022-03-14 00:04:00  37798.49  37822.67  37786.75  37809.06   
...                   ...       ...       ...       ...       ...   
32242 2022-04-05 09:22:00  46669.20  46672.71  46662.72  46670.00   
32243 2022-04-05 09:23:00  46670.00  46670.00  46660.04  46668.52   
32244 2022-04-05 09:24:00  46667.85  46667.85  46644.69  46660.04   
32245 2022-04-05 09:25:00  46657.52  46677.91  46654.39  46676.42   
32246 2022-04-05 09:26:00  46674.53  46692.37  46670.67  46690.77   

            uptrend  downtrend     signal trigger  close_pl  max_pl  max_pct  \
0               NaN        0.0  no_signal     NaN       NaN     NaN      NaN   
1               NaN        NaN  no_signal   nosig       NaN     NaN      NaN   
2               NaN        NaN  no_signal   nosig       NaN     NaN      NaN   
3               NaN        NaN  no_signal   nosig       NaN     NaN      NaN   
4               NaN        NaN  no_signal   nosig       NaN     NaN      NaN   
...             ...        ...        ...     ...       ...     ...      ...   
32242  46619.636668        NaN        buy   nosig     23.25   25.96    0.056   
32243  46619.636668        NaN        buy   nosig     21.77   23.25    0.050   
32244  46619.636668        NaN        buy   nosig     13.29   21.10    0.045   
32245  46619.636668        NaN        buy   nosig     29.67   31.16    0.067   
32246  46628.994140        NaN        buy   nosig     44.02   45.62    0.098   

       max_dd  max_dd_pct  
0         NaN         NaN  
1         NaN         NaN  
2         NaN         NaN  
3         NaN         NaN  
4         NaN         NaN  
...       ...         ...  
32242   15.97       0.034  
32243   13.29       0.028  
32244   -2.06      -0.004  
32245    7.64       0.016  
32246   23.92       0.051  

[32247 rows x 14 columns]

In [746]:
# df_super.drop("max_pct", axis=1, inplace=True)

In [798]:
# Spot Checks and Gen Review of Dataset
print(df_super.shape)
df_super.loc[200:220]
# df_super[df_super.max_pl>175]
df_super[df_super.max_pct>1]

# Query for trade triggers
# trigs = df_super[((df_super.signal=="sell") & (df_super.close_pl==0)) | 
#                  ((df_super.signal=="buy") & (df_super.close_pl==0))]


(15342, 14)


time      open      high       low     close  \
33    2022-03-28 00:33:00  47083.74  47388.00  47064.29  47325.74   
34    2022-03-28 00:34:00  47334.38  47694.00  47311.04  47391.63   
35    2022-03-28 00:35:00  47391.65  47440.37  47309.78  47379.14   
36    2022-03-28 00:36:00  47379.12  47425.58  47280.56  47336.28   
37    2022-03-28 00:37:00  47336.27  47432.92  47321.28  47417.59   
...                   ...       ...       ...       ...       ...   
14456 2022-04-07 00:56:00  42836.91  42868.99  42754.60  42848.07   
14457 2022-04-07 00:57:00  42848.07  42944.50  42820.46  42834.46   
14458 2022-04-07 00:58:00  42834.44  42843.00  42771.91  42819.49   
14459 2022-04-07 00:59:00  42816.80  42907.62  42806.45  42888.68   
14460 2022-04-07 01:00:00  42888.65  42927.69  42866.57  42914.51   

            uptrend     downtrend signal trigger  close_pl  max_pl  max_pct  \
33     46945.178391           NaN    buy   nosig    427.92  490.18    1.045   
34     47134.762052           NaN    buy   nosig    493.81  796.18    1.698   
35     47134.762052           NaN    buy   nosig    481.32  542.55    1.157   
36     47134.762052           NaN    buy   nosig    438.46  527.76    1.125   
37     47134.762052           NaN    buy   nosig    519.77  535.10    1.141   
...             ...           ...    ...     ...       ...     ...      ...   
14456           NaN  43104.985282   sell   nosig    489.87  583.34    1.346   
14457           NaN  43104.985282   sell   nosig    503.48  517.48    1.194   
14458           NaN  43104.985282   sell   nosig    518.45  566.03    1.306   
14459           NaN  43104.985282   sell   nosig    449.26  531.49    1.226   
14460           NaN  43104.985282   sell   nosig    423.43  471.37    1.088   

       max_dd  max_dd_pct  
33     166.47       0.355  
34     413.22       0.881  
35     411.96       0.878  
36     382.74       0.816  
37     423.46       0.903  
...       ...         ...  
14456  468.95       1.082  
14457  393.44       0.908  
14458  494.94       1.142  
14459  430.32       0.993  
14460  410.25       0.947  

[920 rows x 14 columns]

#### SAVE SUPERTREND DATAFRAME TO CSV FILE

In [799]:
# df_super.to_csv("supertrend.csv", index=False)


# Save our new prepped data to csv 
df_super.to_csv("new_prepped.csv", index=False)

#### Continue....

In [748]:
# Build a dataset that contains only the trigger datapoints
trigs = df_super[(df_super.trigger=="sellsig") | (df_super.trigger=="buysig")]

In [749]:
print(trigs.shape)
trigs.head(3)

(912, 12)


time      open      high       low     close       uptrend  \
9  2022-03-14 00:09:00  37723.24  37725.89  37699.00  37712.00           NaN   
16 2022-03-14 00:16:00  37750.61  37846.00  37750.61  37839.84  37616.556977   
84 2022-03-14 01:24:00  38080.27  38094.26  38037.45  38059.44           NaN   

       downtrend signal  trigger  close_pl  max_pl  max_pct  
9   37839.792000   sell  sellsig       0.0     0.0      0.0  
16           NaN    buy   buysig       0.0     0.0      0.0  
84  38218.679324   sell  sellsig       0.0     0.0      0.0

In [750]:
# State the number of trades
trigs.signal.value_counts()

buy     456
sell    456
Name: signal, dtype: int64

#### NARRATIVE
In our available ~13 day scope we have recorded 277 sell signals and 276 buy signals. That's ~42 trades in each 24hr period in our particular dataset. 

We have built the base strategy. We can't really build a stop loss feature at this point as the basic stop loss is triggered on a signal reversal, the stop is built into the strategy i.e. signal reversal also signals the stopout of previous signal!

#### PLAN
We'll build a backtester that uses the following parameters:
1. Take profit levels - TP1:0.3%, TP2:0.6%, TP3: 1%
2. Profit slice - P1: 40%, P2: 40%, P3: 20%
3. If no TP hit; Stop hit on close below uptrend line and close above downtrend line
4. If TP1 hit Stops moved to break even!

#### Written Algorithm
1. Assuming an investment of £100, if our tps are hit we'll remove the profit slice percentage from each position
2. We'll add the profit slices to an interim list
3. When the trade is fully closed we'll tot up the profit slices in the interim list and add to a master list
4. If no tps are hit we take the position value at the stop and add this to the master list
5. Once all trades are reviewed sum up the master list and return the strategy results!!!

In [556]:
# Check a specific trade 
dfx = df_super.loc[trigs.index[0]:trigs.index[1]]

# for index, row in dfx.iterrows():
#     print(index)

dfx
# This is the data points for a single trade it should start with a trigger signal and closepl==0
# It should end with a reversal trigger signal and a switch in the supertrend!!

time      open      high       low     close       uptrend  \
9  2022-03-14 00:09:00  37723.24  37725.89  37699.00  37712.00           NaN   
10 2022-03-14 00:10:00  37712.00  37727.13  37703.99  37721.57           NaN   
11 2022-03-14 00:11:00  37721.57  37725.00  37700.00  37719.75           NaN   
12 2022-03-14 00:12:00  37719.59  37724.30  37680.11  37680.11           NaN   
13 2022-03-14 00:13:00  37683.86  37688.56  37560.40  37630.91           NaN   
14 2022-03-14 00:14:00  37633.93  37644.22  37590.82  37633.30           NaN   
15 2022-03-14 00:15:00  37636.32  37755.30  37627.89  37750.62           NaN   
16 2022-03-14 00:16:00  37750.61  37846.00  37750.61  37839.84  37616.556977   

       downtrend signal  trigger  close_pl  max_pl  max_pct  
9   37839.792000   sell  sellsig      0.00    0.00    0.000  
10  37837.114300   sell    nosig     -9.57    8.01    0.021  
11  37829.398870   sell    nosig     -7.75   12.00    0.032  
12  37820.670983   sell    nosig     31.89   31.89    0.085  
13  37769.547385   sell    nosig     81.09  151.60    0.402  
14  37764.100646   sell    nosig     78.70  121.18    0.321  
15  37764.100646   sell    nosig    -38.62   84.11    0.223  
16           NaN    buy   buysig      0.00    0.00    0.000

In [557]:
for i,j in enumerate(trigs.index[:-1]):
    print(i, j, trigs.index[i+1])

0 9 16
1 16 84
2 84 116
3 116 122
4 122 155
5 155 167
6 167 210
7 210 271
8 271 311
9 311 335
10 335 365
11 365 495
12 495 526
13 526 547
14 547 560
15 560 602
16 602 654
17 654 668
18 668 678
19 678 685
20 685 777
21 777 798
22 798 799
23 799 813
24 813 841
25 841 881
26 881 896
27 896 937
28 937 982
29 982 1012
30 1012 1073
31 1073 1095
32 1095 1132
33 1132 1248
34 1248 1277
35 1277 1300
36 1300 1321
37 1321 1374
38 1374 1393
39 1393 1424
40 1424 1567
41 1567 1628
42 1628 1698
43 1698 1729
44 1729 1757
45 1757 1761
46 1761 1775
47 1775 1833
48 1833 1835
49 1835 1861
50 1861 1927
51 1927 1982
52 1982 1995
53 1995 2057
54 2057 2094
55 2094 2147
56 2147 2177
57 2177 2243
58 2243 2280
59 2280 2387
60 2387 2415
61 2415 2474
62 2474 2510
63 2510 2539
64 2539 2566
65 2566 2625
66 2625 2641
67 2641 2647
68 2647 2717
69 2717 2775
70 2775 2860
71 2860 2874
72 2874 2893
73 2893 2902
74 2902 2914
75 2914 2932
76 2932 2949
77 2949 2980
78 2980 2982
79 2982 3036
80 3036 3165
81 3165 3183
82 3183 3

In [558]:
tp1=0.3
tp2=0.6
tp3=1
p1=40
p2=40
p3=20
        
# Create a list to store each trade result and some other metrics :))
results = []
outcome = []
max_pct_trade = []

# List of trade trigger indexes
trade_idx = trigs.index


# Now we want to loop through the trade indexes and then back test the trades within the index windows
for i,j in enumerate(trade_idx[:-1]):
    # Set our triggers to false
    tp1_hit = False
    tp2_hit = False
    tp3_hit = False


    # Set our capital to £100
    capital = 100

    # Set our profit slices give the strategy parameters
    profit_slices = []


    # Query the trade from our supertrend dataset
    trade = df_super.loc[j:trade_idx[i+1]]
    entry_price = trade.iloc[0].close
    
    # Set a max pct gain tracker for each trade - to be stored in max_pct list
    max_pct_gain = 0

    # Loop through all rows in the isolated trade data
    for index, row in trade.iterrows():
        if row["max_pct"]>max_pct_gain:
            max_pct_gain=row["max_pct"]
        
        
        print("===========================")
        print("Trade index: i{} s{}, f{}, Signal direction {}".format(index, 
                                                                      trade.index[0], 
                                                                      trade.index[-1], 
                                                                      trade.signal.iloc[0]))
        

        # First we calculate the stops and losses

        # If we are on the last candle of the trade and we haven't hit any tps - we have a loser
        # The nature of the data is that the supertrend reversal / stop is hit on the last candle

        if index == trade.index[-1] and tp1_hit==False:

            #### CALCULATE STOP LOSS VALUE AND APEND TO PROFIT SLICE LIST

            ## The stop loss value will be the close price minus the entry price below supertrend for buys
            ## The last index is actually the reversal signal so a buy value means we want to calc our sell stop
            if row["signal"]=="sell":
                # Calculate the stop value of our rekt buy trade and add it to the profit list
                pct_loss = row["close"]/entry_price
                final_position = pct_loss*100
                profit_slices.append(final_position)
                print("buy loss {}".format(final_position))


            elif row["signal"]=="buy":
                # Calculate the stop value of our rekt sell trade and add it to the profit list
                pct_loss = entry_price/row["close"]
                final_position = pct_loss*100
                profit_slices.append(final_position)
                print("sell loss {}".format(final_position))
                
        ## Now what if one or more of our tps have been hit we need to collect the remaining position at stop
        ## First we need to get the percentage price(pp) change from the entry to the supertrend stop
        ## Then we need to take the latest position... take off the tp1/tp2 pct and then take of the pp
        ## Then append this new final position to the profit slices list
        
        elif index == trade.index[-1] and tp2_hit == True and tp3 == False:
            # BUYS ... remember buys have a sell signal on the last row signalling reversal
            if row["signal"]=="sell":
                
                # Calculate buys closing at stop
                tp2_price = entry_price*(1+(tp2/10))
                
                close_price = row["close"]
                
                pct_change = close_price/tp2_price
                
                final_position = capital*pct_change
                # Add to profit slice
                profit_slices.append(final_position)
                
            
            elif row["signal"]=="buy": #sells
                
                # Calculate sells closing at stop
                tp2_price = entry_price*(1-(tp2/10))
                
                close_price = row["close"]
                
                pct_change = tp2_price/close_price
                
                final_position = capital*pct_change
                #Add to profit slice
                profit_slices.append(final_position)
        
            
                    
        
        elif index == trade.index[-1] and tp1_hit == True:
            # BUYS ... remember buys have a sell signal on there last row signalling reversal
            if row["signal"]=="sell":
                
                # Calculate buys closing at stop
                tp1_price = entry_price*(1+(tp1/10))
                
                close_price = row["close"]
                
                pct_change = close_price/tp1_price
                
                final_position = capital*pct_change
                # Add to profit slice
                profit_slices.append(final_position)
                
                
            elif row["signal"]=="buy":
                
                # Calculate sells closing at stop
                tp1_price = entry_price*(1-(tp1/10))
                
                close_price = row["close"]
                
                pct_change = tp1_price/close_price
                
                final_position = capital*pct_change
                #Add to profit slice
                profit_slices.append(final_position)
                
            
                


        # Now we'll calc the tp winners

        # We need to start with an if statement per tp... elifs will break the strategy as a 
        # single candle could pass thro' tp1 to tp2 and we would not bank relevant profits at tp1!

        if row["max_pct"]>=tp1 and tp1_hit==False:
            print(row["max_pct"], tp1)
            tp1_hit=True
            position = capital*(1+(tp1/10))
            profit_take = position*(p1/100)
            print("profit take {}".format(profit_take))
            profit_slices.append(profit_take)
            # new_position = position*((100-p1)/100)
            new_position = position-profit_take
            print("new position {}".format(new_position))
            capital = new_position

        if row["max_pct"]>=tp2 and tp2_hit==False:
            print(row["max_pct"], tp2)
            tp2_hit=True
            position = capital*(1+(tp2/10))
            profit_take = position*(p2/100)
            profit_slices.append(profit_take)
            # new_position = position*((1-p2)/10)
            new_position = position-profit_take
            capital = new_position

        if row["max_pct"]>=tp3 and tp3_hit==False:
            tp3_hit=True
            position = capital*(1+(tp3/10))
            profit_take = position*(p3/100)
            profit_slices.append(profit_take)
            # new_position = position*((1-p3)/10)
            new_position = position-profit_take
            capital = new_position
            
        print(tp1_hit, tp2_hit, tp3_hit)
            
    
    if tp1_hit==True:
        outcome.append("win")
    else:
        outcome.append("loss")
    max_pct_trade.append(max_pct_gain)
    # Append the sum of our profit list to the trade results list
    print(profit_slices)
    results.append(sum(profit_slices))










Trade index: i9 s9, f16, Signal direction sell
False False False
Trade index: i10 s9, f16, Signal direction sell
False False False
Trade index: i11 s9, f16, Signal direction sell
False False False
Trade index: i12 s9, f16, Signal direction sell
False False False
Trade index: i13 s9, f16, Signal direction sell
0.402 0.3
profit take 41.2
new position 61.8
True False False
Trade index: i14 s9, f16, Signal direction sell
True False False
Trade index: i15 s9, f16, Signal direction sell
True False False
Trade index: i16 s9, f16, Signal direction sell
True False False
[41.2, 59.74347544809915]
Trade index: i16 s16, f84, Signal direction buy
False False False
Trade index: i17 s16, f84, Signal direction buy
False False False
Trade index: i18 s16, f84, Signal direction buy
False False False
Trade index: i19 s16, f84, Signal direction buy
False False False
Trade index: i20 s16, f84, Signal direction buy
False False False
Trade index: i21 s16, f84, Signal direction buy
False False False
Trade inde

False False False
Trade index: i382 s365, f495, Signal direction buy
False False False
Trade index: i383 s365, f495, Signal direction buy
False False False
Trade index: i384 s365, f495, Signal direction buy
False False False
Trade index: i385 s365, f495, Signal direction buy
False False False
Trade index: i386 s365, f495, Signal direction buy
False False False
Trade index: i387 s365, f495, Signal direction buy
0.544 0.3
profit take 41.2
new position 61.8
True False False
Trade index: i388 s365, f495, Signal direction buy
True False False
Trade index: i389 s365, f495, Signal direction buy
True False False
Trade index: i390 s365, f495, Signal direction buy
True False False
Trade index: i391 s365, f495, Signal direction buy
True False False
Trade index: i392 s365, f495, Signal direction buy
True False False
Trade index: i393 s365, f495, Signal direction buy
True False False
Trade index: i394 s365, f495, Signal direction buy
True False False
Trade index: i395 s365, f495, Signal direction b

True False False
Trade index: i734 s685, f777, Signal direction sell
True False False
Trade index: i735 s685, f777, Signal direction sell
True False False
Trade index: i736 s685, f777, Signal direction sell
True False False
Trade index: i737 s685, f777, Signal direction sell
True False False
Trade index: i738 s685, f777, Signal direction sell
True False False
Trade index: i739 s685, f777, Signal direction sell
True False False
Trade index: i740 s685, f777, Signal direction sell
0.602 0.6
True True False
Trade index: i741 s685, f777, Signal direction sell
True True False
Trade index: i742 s685, f777, Signal direction sell
True True False
Trade index: i743 s685, f777, Signal direction sell
True True False
Trade index: i744 s685, f777, Signal direction sell
True True False
Trade index: i745 s685, f777, Signal direction sell
True True False
Trade index: i746 s685, f777, Signal direction sell
True True False
Trade index: i747 s685, f777, Signal direction sell
True True False
Trade index: i7

Trade index: i1082 s1073, f1095, Signal direction buy
False False False
Trade index: i1083 s1073, f1095, Signal direction buy
False False False
Trade index: i1084 s1073, f1095, Signal direction buy
False False False
Trade index: i1085 s1073, f1095, Signal direction buy
False False False
Trade index: i1086 s1073, f1095, Signal direction buy
False False False
Trade index: i1087 s1073, f1095, Signal direction buy
False False False
Trade index: i1088 s1073, f1095, Signal direction buy
False False False
Trade index: i1089 s1073, f1095, Signal direction buy
False False False
Trade index: i1090 s1073, f1095, Signal direction buy
False False False
Trade index: i1091 s1073, f1095, Signal direction buy
False False False
Trade index: i1092 s1073, f1095, Signal direction buy
False False False
Trade index: i1093 s1073, f1095, Signal direction buy
False False False
Trade index: i1094 s1073, f1095, Signal direction buy
False False False
Trade index: i1095 s1073, f1095, Signal direction buy
buy loss 9

Trade index: i1412 s1393, f1424, Signal direction buy
False False False
Trade index: i1413 s1393, f1424, Signal direction buy
False False False
Trade index: i1414 s1393, f1424, Signal direction buy
False False False
Trade index: i1415 s1393, f1424, Signal direction buy
False False False
Trade index: i1416 s1393, f1424, Signal direction buy
False False False
Trade index: i1417 s1393, f1424, Signal direction buy
False False False
Trade index: i1418 s1393, f1424, Signal direction buy
False False False
Trade index: i1419 s1393, f1424, Signal direction buy
False False False
Trade index: i1420 s1393, f1424, Signal direction buy
False False False
Trade index: i1421 s1393, f1424, Signal direction buy
False False False
Trade index: i1422 s1393, f1424, Signal direction buy
False False False
Trade index: i1423 s1393, f1424, Signal direction buy
False False False
Trade index: i1424 s1393, f1424, Signal direction buy
buy loss 99.61727550724405
False False False
[99.61727550724405]
Trade index: i142

...

Trade index: i22032 s21996, f22087, Signal direction sell
True False False
Trade index: i22033 s21996, f22087, Signal direction sell
True False False
Trade index: i22034 s21996, f22087, Signal direction sell
True False False
Trade index: i22035 s21996, f22087, Signal direction sell
True False False
Trade index: i22036 s21996, f22087, Signal direction sell
True False False
Trade index: i22037 s21996, f22087, Signal direction sell
True False False
Trade index: i22038 s21996, f22087, Signal direction sell
True False False
Trade index: i22039 s21996, f22087, Signal direction sell
True False False
Trade index: i22040 s21996, f22087, Signal direction sell
True False False
Trade index: i22041 s21996, f22087, Signal direction sell
True False False
Trade index: i22042 s21996, f22087, Signal direction sell
True False False
Trade index: i22043 s21996, f22087, Signal direction sell
True False False
Trade index: i22044 s21996, f22087, Signal direction sell
True False False
Trade index: i22045 s2199

Trade index: i22483 s22467, f22537, Signal direction buy
False False False
Trade index: i22484 s22467, f22537, Signal direction buy
False False False
Trade index: i22485 s22467, f22537, Signal direction buy
False False False
Trade index: i22486 s22467, f22537, Signal direction buy
False False False
Trade index: i22487 s22467, f22537, Signal direction buy
False False False
Trade index: i22488 s22467, f22537, Signal direction buy
False False False
Trade index: i22489 s22467, f22537, Signal direction buy
False False False
Trade index: i22490 s22467, f22537, Signal direction buy
False False False
Trade index: i22491 s22467, f22537, Signal direction buy
False False False
Trade index: i22492 s22467, f22537, Signal direction buy
False False False
Trade index: i22493 s22467, f22537, Signal direction buy
False False False
Trade index: i22494 s22467, f22537, Signal direction buy
False False False
Trade index: i22495 s22467, f22537, Signal direction buy
False False False
Trade index: i22496 s2246

Trade index: i22894 s22892, f22899, Signal direction buy
False False False
Trade index: i22895 s22892, f22899, Signal direction buy
False False False
Trade index: i22896 s22892, f22899, Signal direction buy
False False False
Trade index: i22897 s22892, f22899, Signal direction buy
False False False
Trade index: i22898 s22892, f22899, Signal direction buy
False False False
Trade index: i22899 s22892, f22899, Signal direction buy
buy loss 99.85789401883294
False False False
[99.85789401883294]
Trade index: i22899 s22899, f22958, Signal direction sell
False False False
Trade index: i22900 s22899, f22958, Signal direction sell
False False False
Trade index: i22901 s22899, f22958, Signal direction sell
False False False
Trade index: i22902 s22899, f22958, Signal direction sell
False False False
Trade index: i22903 s22899, f22958, Signal direction sell
False False False
Trade index: i22904 s22899, f22958, Signal direction sell
0.329 0.3
profit take 41.2
new position 61.8
True False False
Tra

Trade index: i23368 s23335, f23376, Signal direction buy
True False False
Trade index: i23369 s23335, f23376, Signal direction buy
True False False
Trade index: i23370 s23335, f23376, Signal direction buy
True False False
Trade index: i23371 s23335, f23376, Signal direction buy
True False False
Trade index: i23372 s23335, f23376, Signal direction buy
0.621 0.6
True True False
Trade index: i23373 s23335, f23376, Signal direction buy
True True False
Trade index: i23374 s23335, f23376, Signal direction buy
True True False
Trade index: i23375 s23335, f23376, Signal direction buy
True True False
Trade index: i23376 s23335, f23376, Signal direction buy
True True False
[41.2, 26.2032, 38.28711418077221]
Trade index: i23376 s23376, f23403, Signal direction sell
False False False
Trade index: i23377 s23376, f23403, Signal direction sell
False False False
Trade index: i23378 s23376, f23403, Signal direction sell
False False False
Trade index: i23379 s23376, f23403, Signal direction sell
False Fa

Trade index: i23750 s23743, f23784, Signal direction sell
False False False
Trade index: i23751 s23743, f23784, Signal direction sell
False False False
Trade index: i23752 s23743, f23784, Signal direction sell
False False False
Trade index: i23753 s23743, f23784, Signal direction sell
False False False
Trade index: i23754 s23743, f23784, Signal direction sell
False False False
Trade index: i23755 s23743, f23784, Signal direction sell
False False False
Trade index: i23756 s23743, f23784, Signal direction sell
False False False
Trade index: i23757 s23743, f23784, Signal direction sell
False False False
Trade index: i23758 s23743, f23784, Signal direction sell
False False False
Trade index: i23759 s23743, f23784, Signal direction sell
False False False
Trade index: i23760 s23743, f23784, Signal direction sell
False False False
Trade index: i23761 s23743, f23784, Signal direction sell
False False False
Trade index: i23762 s23743, f23784, Signal direction sell
False False False
Trade index:

#### EVALUATE THE STRATEGY

In [559]:
# 
returns = sum(results)
break_even = 100*len(results)
gain = returns-break_even
pct_gain = returns/break_even
gain, pct_gain

num_wins = len([x for x in results if x>100])
num_losers = len([x for x in results if x<100])

print("This strategy has returned {}% over {} trades".format(round(pct_gain*100-100,2), len(results)))
print("Winners: {}, Losers: {}".format(num_wins, num_losers))
print("Winrate: {}".format(num_wins/len(results)))
# print("At 10x leverage this is {}%!!".format(round(pct_gain*100-100,2)*10))

This strategy has returned 1.52% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133


In [560]:
sum(results), break_even

(67107.78185009815, 66100)

In [561]:
wins = [x for x in outcome if x == "win"]
losses = [x for x in outcome if x == "loss"]

In [562]:
act_wr = len(wins)/len(outcome)
act_wr

0.3827534039334342

In [564]:
results

[100.94347544809915,
 109.825939056588,
 101.10139593959008,
 99.74330349524179,
 99.52459270638707,
 99.73155350539199,
 99.97323998403328,
 109.92792779646632,
 99.53311272348147,
 99.7141416580561,
 99.80130868648237,
 110.01266619253765,
 99.80418183860766,
 99.71057195434561,
 99.7385457625548,
 105.63244575802403,
 101.2275818043328,
 99.86820629820892,
 99.80472360732288,
 99.73476469539875,
 105.70414409248133,
 101.13293228349863,
 99.68564718510291,
 99.3875646344601,
 99.39321062166735,
 105.57510810402867,
 100.99972484193339,
 101.07995524276188,
 101.0774827276121,
 99.75590701683944,
 105.62204942680177,
 99.70018305102225,
 105.55763656582424,
 105.73950520936795,
 101.19627499501127,
 99.74081882996447,
 99.78463012222434,
 110.12292986268585,
 99.05763001402073,
 99.61727550724405,
 110.15094349693706,
 101.23898520288799,
 105.64983823467367,
 99.83154988274171,
 99.90228641036202,
 99.78864377867808,
 99.79281070146388,
 101.17641475389891,
 99.7330007887561,
 99.51

## WINS AND OUTCOMES NOT ALIGNING

In [565]:
winout = pd.DataFrame({"result":results, "outcome":outcome, 'maxpct':max_pct_trade})
winout.head()

result outcome  maxpct
0  100.943475     win   0.402
1  109.825939     win   1.343
2  101.101396     win   0.408
3   99.743303    loss   0.082
4   99.524593    loss   0.003

In [566]:
# let's check how many rows are affected by this bug
bug = winout[(winout.result<100) & (winout.outcome=="win")]
#bug[bug.maxpct>=0.6]
bug#.maxpct.min()#.result.mean()

Empty DataFrame
Columns: [result, outcome, maxpct]
Index: []

#### NARRATIVE
ALL BUGS OCCUR WHEN WE HAVE ONLY HIT TP1!!

Ok let's debug by checking some of the individual trades that are affected!!

## Hyperparameter tuning of take profit levels and profit margins

In [567]:
tp1s = [0.2, 0.2, 0.2, 0.2, 0.25, 0.25, 0.25, 0.25, 0.3, 0.3, 0.3, 0.3, 0.35, 0.35, 0.35, 0.35]
tp2s = [0.4, 0.5, 0.6, 0.7, 0.4, 0.5, 0.6, 0.7, 0.45, 0.55, 0.65, 0.75, 0.5, 0.65, 0.75, 0.9 ]
tp3s = [0.6, 0.7, 0.8, 1.0, 0.6, 0.7, 0.8, 1.0, 0.65, 0.75, 0.85, 1.0, 0.8, 0.9, 1.0, 1.1]

p1s = [70, 60, 60, 50, 50, 50, 40, 40, 40, 40, 30, 30, 30, 30, 20, 20, 20, 20]
p2s = [20, 20, 30, 40, 30, 20, 40, 30, 20, 10, 60, 50, 40, 30, 60, 50, 40, 30]
p3s = [10, 20, 10, 10, 20, 30, 20, 30, 40, 50, 10, 20, 30, 40, 20, 30, 40, 50]

In [568]:
# Check our profit takes add up to 100??
for i, (j, k, l) in enumerate(zip(p1s, p2s, p3s)):
    if j+k+l != 100:
        print("not 100")
    elif i == len(p1s)-1:
        print("We good!")
# Check our tp lists are all the same length
if len(tp1s)==len(tp2s)==len(tp3s):
    print("TP levels equal")
else:
    print("Review tp value list lengths!")

We good!
TP levels equal


Ok! We want to loop through all the tp combinations and for each iteration loop through all the profit take combinations. 

In [569]:
# How many results sets will this method generate?
len(tp1s)*len(p1s)

288

In [570]:
list_of_combos = []
for tp, (tp1, tp2, tp3) in enumerate(zip(tp1s, tp2s, tp3s)):
    for p, (p1, p2, p3) in enumerate(zip(p1s, p2s, p3s)):
        list_of_combos.append([tp1, tp2, tp3, p1, p2, p3])

In [571]:
cols = ["tp1", "tp2", "tp3", "p1", "p2", "p3"]
pd.DataFrame(list_of_combos, columns=cols)

tp1  tp2  tp3  p1  p2  p3
0    0.20  0.4  0.6  70  20  10
1    0.20  0.4  0.6  60  20  20
2    0.20  0.4  0.6  60  30  10
3    0.20  0.4  0.6  50  40  10
4    0.20  0.4  0.6  50  30  20
..    ...  ...  ...  ..  ..  ..
283  0.35  0.9  1.1  30  30  40
284  0.35  0.9  1.1  20  60  20
285  0.35  0.9  1.1  20  50  30
286  0.35  0.9  1.1  20  40  40
287  0.35  0.9  1.1  20  30  50

[288 rows x 6 columns]

In [592]:
list_of_combos = []
winrates = []
pct_returns = []
sum_wins = []
for tp, (tp1, tp2, tp3) in enumerate(zip(tp1s, tp2s, tp3s)):
    for p, (p1, p2, p3) in enumerate(zip(p1s, p2s, p3s)):
        list_of_combos.append([tp1, tp2, tp3, p1, p2, p3])
        
        # Create a list to store each trade result and some other metrics :))
        results = []
        outcome = []
        max_pct_trade = []

        # List of trade trigger indexes
        trade_idx = trigs.index


        # Now we want to loop through the trade indexes and then back test the trades within the index windows
        for i,j in enumerate(trade_idx[:-1]):
            # Set our triggers to false
            tp1_hit = False
            tp2_hit = False
            tp3_hit = False


            # Set our capital to £100
            capital = 100

            # Set our profit slices give the strategy parameters
            profit_slices = []


            # Query the trade from our supertrend dataset
            trade = df_super.loc[j:trade_idx[i+1]]
            entry_price = trade.iloc[0].close

            # Set a max pct gain tracker for each trade - to be stored in max_pct list
            max_pct_gain = 0

            # Loop through all rows in the isolated trade data
            for index, row in trade.iterrows():
                if row["max_pct"]>max_pct_gain:
                    max_pct_gain=row["max_pct"]


                #print("===========================")
                #print("Trade index: i{} s{}, f{}, Signal direction {}".format(index, 
#                                                                               trade.index[0], 
#                                                                               trade.index[-1], 
#                                                                               trade.signal.iloc[0]))


                # First we calculate the stops and losses

                # If we are on the last candle of the trade and we haven't hit any tps - we have a loser
                # The nature of the data is that the supertrend reversal / stop is hit on the last candle

                if index == trade.index[-1] and tp1_hit==False:

                    #### CALCULATE STOP LOSS VALUE AND APEND TO PROFIT SLICE LIST

                    ## The stop loss value will be the close price minus the entry price below supertrend for buys
                    ## The last index is actually the reversal signal so a buy value means we want to calc our sell stop
                    if row["signal"]=="sell":
                        # Calculate the stop value of our rekt buy trade and add it to the profit list
                        pct_loss = row["close"]/entry_price
                        final_position = pct_loss*100
                        profit_slices.append(final_position)
                        #print("buy loss {}".format(final_position))


                    elif row["signal"]=="buy":
                        # Calculate the stop value of our rekt sell trade and add it to the profit list
                        pct_loss = entry_price/row["close"]
                        final_position = pct_loss*100
                        profit_slices.append(final_position)
                        #print("sell loss {}".format(final_position))

                ## Now what if one or more of our tps have been hit we need to collect the remaining position at stop
                ## First we need to get the percentage price(pp) change from the entry to the supertrend stop
                ## Then we need to take the latest position... take off the tp1/tp2 pct and then take of the pp
                ## Then append this new final position to the profit slices list

                elif index == trade.index[-1] and tp2_hit == True and tp3 == False:
                    # BUYS ... remember buys have a sell signal on the last row signalling reversal
                    if row["signal"]=="sell":

                        # Calculate buys closing at stop
                        tp2_price = entry_price*(1+(tp2/10))

                        close_price = row["close"]

                        pct_change = close_price/tp2_price

                        final_position = capital*pct_change
                        # Add to profit slice
                        profit_slices.append(final_position)


                    elif row["signal"]=="buy": #sells

                        # Calculate sells closing at stop
                        tp2_price = entry_price*(1-(tp2/10))

                        close_price = row["close"]

                        pct_change = tp2_price/close_price

                        final_position = capital*pct_change
                        #Add to profit slice
                        profit_slices.append(final_position)




                elif index == trade.index[-1] and tp1_hit == True:
                    # BUYS ... remember buys have a sell signal on there last row signalling reversal
                    if row["signal"]=="sell":

                        # Calculate buys closing at stop
                        tp1_price = entry_price*(1+(tp1/10))

                        close_price = row["close"]

                        pct_change = close_price/tp1_price

                        final_position = capital*pct_change
                        # Add to profit slice
                        profit_slices.append(final_position)


                    elif row["signal"]=="buy":

                        # Calculate sells closing at stop
                        tp1_price = entry_price*(1-(tp1/10))

                        close_price = row["close"]

                        pct_change = tp1_price/close_price

                        final_position = capital*pct_change
                        #Add to profit slice
                        profit_slices.append(final_position)





                # Now we'll calc the tp winners

                # We need to start with an if statement per tp... elifs will break the strategy as a 
                # single candle could pass thro' tp1 to tp2 and we would not bank relevant profits at tp1!

                if row["max_pct"]>=tp1 and tp1_hit==False:
                    #print(row["max_pct"], tp1)
                    tp1_hit=True
                    position = capital*(1+(tp1/10))
                    profit_take = position*(p1/100)
                    #print("profit take {}".format(profit_take))
                    profit_slices.append(profit_take)
                    # new_position = position*((100-p1)/100)
                    new_position = position-profit_take
                    #print("new position {}".format(new_position))
                    capital = new_position

                if row["max_pct"]>=tp2 and tp2_hit==False:
                    #print(row["max_pct"], tp2)
                    tp2_hit=True
                    position = capital*(1+(tp2/10))
                    profit_take = position*(p2/100)
                    profit_slices.append(profit_take)
                    # new_position = position*((1-p2)/10)
                    new_position = position-profit_take
                    capital = new_position

                if row["max_pct"]>=tp3 and tp3_hit==False:
                    tp3_hit=True
                    position = capital*(1+(tp3/10))
                    profit_take = position*(p3/100)
                    profit_slices.append(profit_take)
                    # new_position = position*((1-p3)/10)
                    new_position = position-profit_take
                    capital = new_position

                #print(tp1_hit, tp2_hit, tp3_hit)


            if tp1_hit==True:
                outcome.append("win")
            else:
                outcome.append("loss")
            max_pct_trade.append(max_pct_gain)
            # Append the sum of our profit list to the trade results list
            #print(profit_slices)
            results.append(sum(profit_slices))


        # Produce report of these trade parameters and add to summary metrics:
        returns = sum(results)
        break_even = 100*len(results)
        gain = returns-break_even
        pct_gain = returns/break_even
    
        num_wins = len([x for x in results if x>100])
        num_losers = len([x for x in results if x<100])
        
        winrate = num_wins/len(results)
        pct_return = round(pct_gain*100-100,2)
        winrates.append(winrate)
        pct_returns.append(pct_return)
        wins = [x for x in results if x>100]
        sum_wins.append(sum(wins))
        print("==================================================")
        print(tp1, tp2, tp3, p1, p2, p3)
        print("This strategy has returned {}% over {} trades".format(pct_return, len(results)))
        print("Winners: {}, Losers: {}".format(num_wins, num_losers))
        print("Winrate: {}".format(winrate))
        print("Sum of all wins: {}".format(sum(wins)))
        # print("At 10x leverage this is {}%!!".format(round(pct_gain*100-100,2)*10))



0.2 0.4 0.6 70 20 10
This strategy has returned 1.29% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34128.849059873326
0.2 0.4 0.6 60 20 20
This strategy has returned 1.44% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34225.55687006985
0.2 0.4 0.6 60 30 10
This strategy has returned 1.4% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34198.8863035422
0.2 0.4 0.6 50 40 10
This strategy has returned 1.49% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34258.812348736574
0.2 0.4 0.6 50 30 20
This strategy has returned 1.54% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34291.14303039943
0.2 0.4 0.6 50 20 30
This strategy has returned 1.59% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34325.488765055634
0.2 0.4 0.6 40 40 20
This strategy has return

0.2 0.6 0.8 50 40 10
This strategy has returned 1.41% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34209.083022101
0.2 0.6 0.8 50 30 20
This strategy has returned 1.46% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34240.50974307686
0.2 0.6 0.8 50 20 30
This strategy has returned 1.51% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34273.13594614751
0.2 0.6 0.8 40 40 20
This strategy has returned 1.53% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34283.60373445851
0.2 0.6 0.8 40 30 30
This strategy has returned 1.58% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34322.03548888644
0.2 0.6 0.8 40 20 40
This strategy has returned 1.64% over 661 trades
Winners: 332, Losers: 329
Winrate: 0.5022692889561271
Sum of all wins: 34361.906621828064
0.2 0.6 0.8 40 10 50
This strategy has returned

0.25 0.4 0.6 40 40 20
This strategy has returned 1.71% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31206.482060848735
0.25 0.4 0.6 40 30 30
This strategy has returned 1.76% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31244.2564281161
0.25 0.4 0.6 40 20 40
This strategy has returned 1.83% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31285.313154651452
0.25 0.4 0.6 40 10 50
This strategy has returned 1.89% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31329.652240454692
0.25 0.4 0.6 30 60 10
This strategy has returned 1.72% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31216.462166609774
0.25 0.4 0.6 30 50 20
This strategy has returned 1.78% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31254.788133036218
0.25 0.4 0.6 30 40 30
This str

0.25 0.6 0.8 40 10 50
This strategy has returned 1.77% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31251.360133055514
0.25 0.6 0.8 30 60 10
This strategy has returned 1.59% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31127.031332662686
0.25 0.6 0.8 30 50 20
This strategy has returned 1.65% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31166.57760633975
0.25 0.6 0.8 30 40 30
This strategy has returned 1.71% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31208.496663840575
0.25 0.6 0.8 30 30 40
This strategy has returned 1.78% over 661 trades
Winners: 300, Losers: 361
Winrate: 0.45385779122541603
Sum of all wins: 31252.788505165197
0.25 0.6 0.8 20 60 20
This strategy has returned 1.68% over 661 trades
Winners: 299, Losers: 362
Winrate: 0.4523449319213313
Sum of all wins: 31088.975851440937
0.25 0.6 0.8 20 50 30
This str

0.3 0.45 0.65 30 40 30
This strategy has returned 1.86% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28712.561499072657
0.3 0.45 0.65 30 30 40
This strategy has returned 1.93% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28756.31322032268
0.3 0.45 0.65 20 60 20
This strategy has returned 1.87% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28715.854704720674
0.3 0.45 0.65 20 50 30
This strategy has returned 1.93% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28758.5547794253
0.3 0.45 0.65 20 40 40
This strategy has returned 2.0% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28806.122782422117
0.3 0.45 0.65 20 30 50
This strategy has returned 2.08% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28858.558713711078
0.3 0.55 0.75 70 20 10
This stra

0.3 0.65 0.85 20 50 30
This strategy has returned 1.74% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28630.31716002709
0.3 0.65 0.85 20 40 40
This strategy has returned 1.81% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28678.337730301242
0.3 0.65 0.85 20 30 50
This strategy has returned 1.89% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28729.554240843565
0.3 0.75 1.0 70 20 10
This strategy has returned 1.25% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28310.877754369703
0.3 0.75 1.0 60 20 20
This strategy has returned 1.33% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28364.940668252093
0.3 0.75 1.0 60 30 10
This strategy has returned 1.31% over 661 trades
Winners: 274, Losers: 387
Winrate: 0.4145234493192133
Sum of all wins: 28348.232419092797
0.3 0.75 1.0 50 40 10
This strat

0.35 0.65 0.9 70 20 10
This strategy has returned 1.33% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26566.555497247515
0.35 0.65 0.9 60 20 20
This strategy has returned 1.44% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26639.414121388436
0.35 0.65 0.9 60 30 10
This strategy has returned 1.41% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26619.67044308547
0.35 0.65 0.9 50 40 10
This strategy has returned 1.48% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26666.291731394416
0.35 0.65 0.9 50 30 20
This strategy has returned 1.52% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26689.91564751612
0.35 0.65 0.9 50 20 30
This strategy has returned 1.56% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26715.650927151833
0.35 0.65 0.9 40 40 20
T

0.35 0.9 1.1 50 40 10
This strategy has returned 1.28% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26531.43229913814
0.35 0.9 1.1 50 30 20
This strategy has returned 1.31% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26553.32837615483
0.35 0.9 1.1 50 20 30
This strategy has returned 1.35% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26576.5106126761
0.35 0.9 1.1 40 40 20
This strategy has returned 1.34% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26568.69919027041
0.35 0.9 1.1 40 30 30
This strategy has returned 1.38% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26595.74617839317
0.35 0.9 1.1 40 20 40
This strategy has returned 1.42% over 661 trades
Winners: 256, Losers: 405
Winrate: 0.38729198184568836
Sum of all wins: 26624.336557921422
0.35 0.9 1.1 40 10 50
This strateg

In [597]:
# Build a dataset to review each trade's metrics
cols = ["tp1", "tp2", "tp3", "p1", "p2", "p3"]
res_df = pd.DataFrame(list_of_combos, columns=cols)
res_df["winrate"]=winrates
res_df["return"]=pct_returns
res_df["win_val"]=sum_wins
res_df["win_gain"]= res_df["win_val"]/(((256+405)*res_df["winrate"])*100)

In [598]:
print(res_df.shape)
res_df.head()

(288, 10)


tp1  tp2  tp3  p1  p2  p3   winrate  return       win_val  win_gain
0  0.2  0.4  0.6  70  20  10  0.502269    1.29  34128.849060  1.027977
1  0.2  0.4  0.6  60  20  20  0.502269    1.44  34225.556870  1.030890
2  0.2  0.4  0.6  60  30  10  0.502269    1.40  34198.886304  1.030087
3  0.2  0.4  0.6  50  40  10  0.502269    1.49  34258.812349  1.031892
4  0.2  0.4  0.6  50  30  20  0.502269    1.54  34291.143030  1.032866

In [603]:
res_df[res_df["return"]>1.95]

tp1   tp2   tp3  p1  p2  p3   winrate  return       win_val  win_gain
17   0.20  0.40  0.60  20  30  50  0.499244    1.98  34385.105033  1.041973
88   0.25  0.40  0.60  20  40  40  0.452345    1.98  31290.867138  1.046517
89   0.25  0.40  0.60  20  30  50  0.452345    2.07  31345.609440  1.048348
107  0.25  0.50  0.70  20  30  50  0.452345    1.98  31289.080912  1.046458
160  0.30  0.45  0.65  20  40  40  0.414523    2.00  28806.122782  1.051318
161  0.30  0.45  0.65  20  30  50  0.414523    2.08  28858.558714  1.053232
179  0.30  0.55  0.75  20  30  50  0.414523    1.98  28793.887024  1.050872
232  0.35  0.50  0.80  20  40  40  0.387292    1.99  26997.957184  1.054608
233  0.35  0.50  0.80  20  30  50  0.387292    2.05  27038.819908  1.056204

In [606]:
res_df[res_df["return"]<1.30].sort_values(by="return")

tp1   tp2  tp3  p1  p2  p3   winrate  return       win_val  win_gain
54   0.20  0.70  1.0  70  20  10  0.502269    1.15  34034.002216  1.025121
56   0.20  0.70  1.0  60  30  10  0.502269    1.21  34076.504208  1.026401
270  0.35  0.90  1.1  70  20  10  0.387292    1.21  26487.032288  1.034650
126  0.25  0.70  1.0  70  20  10  0.453858    1.23  30890.629150  1.029688
55   0.20  0.70  1.0  60  20  20  0.502269    1.24  34094.432907  1.026941
36   0.20  0.60  0.8  70  20  10  0.502269    1.25  34101.352109  1.027149
198  0.30  0.75  1.0  70  20  10  0.414523    1.25  28310.877754  1.033244
272  0.35  0.90  1.1  60  30  10  0.387292    1.25  26512.711197  1.035653
57   0.20  0.70  1.0  50  40  10  0.502269    1.26  34110.935183  1.027438
252  0.35  0.75  1.0  70  20  10  0.387292    1.26  26520.354795  1.035951
18   0.20  0.50  0.7  70  20  10  0.502269    1.27  34115.340724  1.027571
271  0.35  0.90  1.1  60  20  20  0.387292    1.28  26530.742523  1.036357
273  0.35  0.90  1.1  50  40  10  0.387292    1.28  26531.432299  1.036384
0    0.20  0.40  0.6  70  20  10  0.502269    1.29  34128.849060  1.027977
128  0.25  0.70  1.0  60  30  10  0.453858    1.29  30929.235369  1.030975

In [600]:
res_df[res_df.win_gain>1.05]

tp1   tp2   tp3  p1  p2  p3   winrate  return       win_val  win_gain
160  0.30  0.45  0.65  20  40  40  0.414523    2.00  28806.122782  1.051318
161  0.30  0.45  0.65  20  30  50  0.414523    2.08  28858.558714  1.053232
179  0.30  0.55  0.75  20  30  50  0.414523    1.98  28793.887024  1.050872
225  0.35  0.50  0.80  40  10  50  0.387292    1.86  26913.275536  1.051300
228  0.35  0.50  0.80  30  40  30  0.387292    1.85  26908.046157  1.051096
229  0.35  0.50  0.80  30  30  40  0.387292    1.90  26941.934796  1.052419
230  0.35  0.50  0.80  20  60  20  0.387292    1.88  26929.028843  1.051915
231  0.35  0.50  0.80  20  50  30  0.387292    1.93  26961.360162  1.053178
232  0.35  0.50  0.80  20  40  40  0.387292    1.99  26997.957184  1.054608
233  0.35  0.50  0.80  20  30  50  0.387292    2.05  27038.819908  1.056204
251  0.35  0.65  0.90  20  30  50  0.387292    1.87  26918.386714  1.051499

#### NARRATIVE
After hyperparamter tuning our best return is 2.05% from 549 trades. From an initial £100 investment we would have £102.50 after the trade period of 13days. After fees and spread this paultry return would be further eroded and would possibly even invert into a loss. Note that this is also with 10x leverage. At best we can say the strategy breaks even. 

#### Review
1. All the best results are p3 heavy, i.e. we take the majority of our profit from our tp3 level.
2. The best results have a relatively narrow spread of tps... the best result has all tps within a 0.35% range from 0.3 to 0.65. 
3. The winrates are in and around the expected 40% wins seen in the original chart back tests. 
4. The top 3 returns all have profit split of 20,30,50. This is the min take at TP1 and Max take at TP3. 
5. The bottom returns generally have a 70/60, 20/30, 10 split. 

#### Next steps
1. Let's rejig the hyperparameter and shift the Ps up to take the advice from the initial run. 
1. Backtest with trailing stops
2. Build a classifier to state whether we can expect a win / loss from a trade signal! Consider indicators. 
3. Run the best performer and spot check the scores

#### SUMMARY OF INITIAL HYPER PARAMETER RESULTS

![alt text](HP_Summary.png "Summary of Results")

In [608]:
tp1s = [0.20, 0.22, 0.24, 0.26, 0.28, 0.30, 0.32, 0.34, 0.36, 0.38]
tp2s = [0.40, 0.44, 0.48, 0.5, 0.54, 0.58]
tp3s = [0.60, 0.65, 0.7, 0.75, 0.8, 0.85, 0.90]

p1s = [1, 5, 10, 10, 10, 20, 20, 20, 20, 25, 25]
p2s = [1, 10, 10, 20, 30, 5, 10, 20, 30, 10, 20]
p3s = [98, 85, 80, 70, 60, 85, 70, 60, 50, 65, 55]

In [609]:
list_of_combos = []
winrates = []
pct_returns = []
sum_wins = []
for tp1 in tp1s:
    for tp2 in tp2s:
        for tp3 in tp3s:
            for p, (p1, p2, p3) in enumerate(zip(p1s, p2s, p3s)):
                list_of_combos.append([tp1, tp2, tp3, p1, p2, p3])

                # Create a list to store each trade result and some other metrics :))
                results = []
                outcome = []
                max_pct_trade = []

                # List of trade trigger indexes
                trade_idx = trigs.index


                # Now we want to loop through the trade indexes and then back test the trades within the index windows
                for i,j in enumerate(trade_idx[:-1]):
                    # Set our triggers to false
                    tp1_hit = False
                    tp2_hit = False
                    tp3_hit = False


                    # Set our capital to £100
                    capital = 100

                    # Set our profit slices give the strategy parameters
                    profit_slices = []


                    # Query the trade from our supertrend dataset
                    trade = df_super.loc[j:trade_idx[i+1]]
                    entry_price = trade.iloc[0].close

                    # Set a max pct gain tracker for each trade - to be stored in max_pct list
                    max_pct_gain = 0

                    # Loop through all rows in the isolated trade data
                    for index, row in trade.iterrows():
                        if row["max_pct"]>max_pct_gain:
                            max_pct_gain=row["max_pct"]


                        #print("===========================")
                        #print("Trade index: i{} s{}, f{}, Signal direction {}".format(index, 
        #                                                                               trade.index[0], 
        #                                                                               trade.index[-1], 
        #                                                                               trade.signal.iloc[0]))


                        # First we calculate the stops and losses

                        # If we are on the last candle of the trade and we haven't hit any tps - we have a loser
                        # The nature of the data is that the supertrend reversal / stop is hit on the last candle

                        if index == trade.index[-1] and tp1_hit==False:

                            #### CALCULATE STOP LOSS VALUE AND APEND TO PROFIT SLICE LIST

                            ## The stop loss value will be the close price minus the entry price below supertrend for buys
                            ## The last index is actually the reversal signal so a buy value means we want to calc our sell stop
                            if row["signal"]=="sell":
                                # Calculate the stop value of our rekt buy trade and add it to the profit list
                                pct_loss = row["close"]/entry_price
                                final_position = pct_loss*100
                                profit_slices.append(final_position)
                                #print("buy loss {}".format(final_position))


                            elif row["signal"]=="buy":
                                # Calculate the stop value of our rekt sell trade and add it to the profit list
                                pct_loss = entry_price/row["close"]
                                final_position = pct_loss*100
                                profit_slices.append(final_position)
                                #print("sell loss {}".format(final_position))

                        ## Now what if one or more of our tps have been hit we need to collect the remaining position at stop
                        ## First we need to get the percentage price(pp) change from the entry to the supertrend stop
                        ## Then we need to take the latest position... take off the tp1/tp2 pct and then take of the pp
                        ## Then append this new final position to the profit slices list

                        elif index == trade.index[-1] and tp2_hit == True and tp3 == False:
                            # BUYS ... remember buys have a sell signal on the last row signalling reversal
                            if row["signal"]=="sell":

                                # Calculate buys closing at stop
                                tp2_price = entry_price*(1+(tp2/10))

                                close_price = row["close"]

                                pct_change = close_price/tp2_price

                                final_position = capital*pct_change
                                # Add to profit slice
                                profit_slices.append(final_position)


                            elif row["signal"]=="buy": #sells

                                # Calculate sells closing at stop
                                tp2_price = entry_price*(1-(tp2/10))

                                close_price = row["close"]

                                pct_change = tp2_price/close_price

                                final_position = capital*pct_change
                                #Add to profit slice
                                profit_slices.append(final_position)




                        elif index == trade.index[-1] and tp1_hit == True:
                            # BUYS ... remember buys have a sell signal on there last row signalling reversal
                            if row["signal"]=="sell":

                                # Calculate buys closing at stop
                                tp1_price = entry_price*(1+(tp1/10))

                                close_price = row["close"]

                                pct_change = close_price/tp1_price

                                final_position = capital*pct_change
                                # Add to profit slice
                                profit_slices.append(final_position)


                            elif row["signal"]=="buy":

                                # Calculate sells closing at stop
                                tp1_price = entry_price*(1-(tp1/10))

                                close_price = row["close"]

                                pct_change = tp1_price/close_price

                                final_position = capital*pct_change
                                #Add to profit slice
                                profit_slices.append(final_position)





                        # Now we'll calc the tp winners

                        # We need to start with an if statement per tp... elifs will break the strategy as a 
                        # single candle could pass thro' tp1 to tp2 and we would not bank relevant profits at tp1!

                        if row["max_pct"]>=tp1 and tp1_hit==False:
                            #print(row["max_pct"], tp1)
                            tp1_hit=True
                            position = capital*(1+(tp1/10))
                            profit_take = position*(p1/100)
                            #print("profit take {}".format(profit_take))
                            profit_slices.append(profit_take)
                            # new_position = position*((100-p1)/100)
                            new_position = position-profit_take
                            #print("new position {}".format(new_position))
                            capital = new_position

                        if row["max_pct"]>=tp2 and tp2_hit==False:
                            #print(row["max_pct"], tp2)
                            tp2_hit=True
                            position = capital*(1+(tp2/10))
                            profit_take = position*(p2/100)
                            profit_slices.append(profit_take)
                            # new_position = position*((1-p2)/10)
                            new_position = position-profit_take
                            capital = new_position

                        if row["max_pct"]>=tp3 and tp3_hit==False:
                            tp3_hit=True
                            position = capital*(1+(tp3/10))
                            profit_take = position*(p3/100)
                            profit_slices.append(profit_take)
                            # new_position = position*((1-p3)/10)
                            new_position = position-profit_take
                            capital = new_position

                        #print(tp1_hit, tp2_hit, tp3_hit)


                    if tp1_hit==True:
                        outcome.append("win")
                    else:
                        outcome.append("loss")
                    max_pct_trade.append(max_pct_gain)
                    # Append the sum of our profit list to the trade results list
                    #print(profit_slices)
                    results.append(sum(profit_slices))


                # Produce report of these trade parameters and add to summary metrics:
                returns = sum(results)
                break_even = 100*len(results)
                gain = returns-break_even
                pct_gain = returns/break_even

                num_wins = len([x for x in results if x>100])
                num_losers = len([x for x in results if x<100])

                winrate = num_wins/len(results)
                pct_return = round(pct_gain*100-100,2)
                winrates.append(winrate)
                pct_returns.append(pct_return)
                wins = [x for x in results if x>100]
                sum_wins.append(sum(wins))
                print("==================================================")
                print(tp1, tp2, tp3, p1, p2, p3)
                print("This strategy has returned {}% over {} trades".format(pct_return, len(results)))
                print("Winners: {}, Losers: {}".format(num_wins, num_losers))
                print("Winrate: {}".format(winrate))
                print("Sum of all wins: {}".format(sum(wins)))
        # print("At 10x leverage this is {}%!!".format(round(pct_gain*100-100,2)*10))

0.2 0.4 0.6 1 1 98
This strategy has returned 2.64% over 661 trades
Winners: 242, Losers: 419
Winrate: 0.3661119515885023
Sum of all wins: 26031.671803413636
0.2 0.4 0.6 5 10 85
This strategy has returned 2.45% over 661 trades
Winners: 282, Losers: 379
Winrate: 0.4266263237518911
Sum of all wins: 29897.780942294197
0.2 0.4 0.6 10 10 80
This strategy has returned 2.35% over 661 trades
Winners: 315, Losers: 346
Winrate: 0.47655068078668683
Sum of all wins: 33131.90546079695
0.2 0.4 0.6 10 20 70
This strategy has returned 2.24% over 661 trades
Winners: 315, Losers: 346
Winrate: 0.47655068078668683
Sum of all wins: 33059.201852251834
0.2 0.4 0.6 10 30 60
This strategy has returned 2.14% over 661 trades
Winners: 315, Losers: 346
Winrate: 0.47655068078668683
Sum of all wins: 32990.12533909472
0.2 0.4 0.6 20 5 85
This strategy has returned 2.24% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34555.93785125894
0.2 0.4 0.6 20 10 70
This strategy has retu

0.2 0.4 0.75 20 10 70
This strategy has returned 2.04% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34421.05764820136
0.2 0.4 0.75 20 20 60
This strategy has returned 1.96% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34372.07981515894
0.2 0.4 0.75 20 30 50
This strategy has returned 1.89% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34325.22968038847
0.2 0.4 0.75 25 10 65
This strategy has returned 1.96% over 661 trades
Winners: 331, Losers: 330
Winrate: 0.5007564296520424
Sum of all wins: 34468.75459713941
0.2 0.4 0.75 25 20 55
This strategy has returned 1.89% over 661 trades
Winners: 331, Losers: 330
Winrate: 0.5007564296520424
Sum of all wins: 34423.33655794466
0.2 0.4 0.8 1 1 98
This strategy has returned 2.38% over 661 trades
Winners: 242, Losers: 419
Winrate: 0.3661119515885023
Sum of all wins: 25862.30492894583
0.2 0.4 0.8 5 10 85
This strategy has re

0.2 0.44 0.6 5 10 85
This strategy has returned 2.44% over 661 trades
Winners: 276, Losers: 385
Winrate: 0.4175491679273828
Sum of all wins: 29291.81549463404
0.2 0.44 0.6 10 10 80
This strategy has returned 2.34% over 661 trades
Winners: 312, Losers: 349
Winrate: 0.4720121028744327
Sum of all wins: 32825.80740850906
0.2 0.44 0.6 10 20 70
This strategy has returned 2.23% over 661 trades
Winners: 312, Losers: 349
Winrate: 0.4720121028744327
Sum of all wins: 32749.224321264734
0.2 0.44 0.6 10 30 60
This strategy has returned 2.12% over 661 trades
Winners: 312, Losers: 349
Winrate: 0.4720121028744327
Sum of all wins: 32676.28227977525
0.2 0.44 0.6 20 5 85
This strategy has returned 2.23% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34552.05727293876
0.2 0.44 0.6 20 10 70
This strategy has returned 2.16% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34502.24248033683
0.2 0.44 0.6 20 20 60
This strategy has

0.2 0.44 0.75 20 20 60
This strategy has returned 1.95% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34362.69229129868
0.2 0.44 0.75 20 30 50
This strategy has returned 1.87% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34312.4620975372
0.2 0.44 0.75 25 10 65
This strategy has returned 1.95% over 661 trades
Winners: 331, Losers: 330
Winrate: 0.5007564296520424
Sum of all wins: 34463.113008838256
0.2 0.44 0.75 25 20 55
This strategy has returned 1.88% over 661 trades
Winners: 331, Losers: 330
Winrate: 0.5007564296520424
Sum of all wins: 34414.52041034771
0.2 0.44 0.8 1 1 98
This strategy has returned 2.38% over 661 trades
Winners: 235, Losers: 426
Winrate: 0.3555219364599092
Sum of all wins: 25159.842190392745
0.2 0.44 0.8 5 10 85
This strategy has returned 2.23% over 661 trades
Winners: 276, Losers: 385
Winrate: 0.4175491679273828
Sum of all wins: 29152.850804783477
0.2 0.44 0.8 10 10 80
This strategy

0.2 0.48 0.6 10 10 80
This strategy has returned 2.36% over 661 trades
Winners: 312, Losers: 349
Winrate: 0.4720121028744327
Sum of all wins: 32837.42943394673
0.2 0.48 0.6 10 20 70
This strategy has returned 2.24% over 661 trades
Winners: 312, Losers: 349
Winrate: 0.4720121028744327
Sum of all wins: 32758.40275831884
0.2 0.48 0.6 10 30 60
This strategy has returned 2.13% over 661 trades
Winners: 312, Losers: 349
Winrate: 0.4720121028744327
Sum of all wins: 32683.03107881268
0.2 0.48 0.6 20 5 85
This strategy has returned 2.25% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34563.47865162057
0.2 0.48 0.6 20 10 70
This strategy has returned 2.17% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34512.51736814728
0.2 0.48 0.6 20 20 60
This strategy has returned 2.07% over 661 trades
Winners: 330, Losers: 331
Winrate: 0.49924357034795763
Sum of all wins: 34443.8958769766
0.2 0.48 0.6 20 30 50
This strategy has

...

0.38 0.5 0.85 10 10 80
This strategy has returned 2.36% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26142.441372830504
0.38 0.5 0.85 10 20 70
This strategy has returned 2.28% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26090.20720534363
0.38 0.5 0.85 10 30 60
This strategy has returned 2.2% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26042.8300502155
0.38 0.5 0.85 20 5 85
This strategy has returned 2.24% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26169.049275198297
0.38 0.5 0.85 20 10 70
This strategy has returned 2.18% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26124.787036094018
0.38 0.5 0.85 20 20 60
This strategy has returned 2.11% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26080.51533715402
0.38 0.5 0.85 20 30 50
This str

0.38 0.54 0.65 20 30 50
This strategy has returned 2.15% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26104.73634283274
0.38 0.54 0.65 25 10 65
This strategy has returned 2.25% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26173.65696033667
0.38 0.54 0.65 25 20 55
This strategy has returned 2.15% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26107.383296023887
0.38 0.54 0.7 1 1 98
This strategy has returned 2.79% over 661 trades
Winners: 224, Losers: 437
Winrate: 0.3388804841149773
Sum of all wins: 24335.357036626407
0.38 0.54 0.7 5 10 85
This strategy has returned 2.58% over 661 trades
Winners: 239, Losers: 422
Winrate: 0.3615733736762481
Sum of all wins: 25694.12058066357
0.38 0.54 0.7 10 10 80
This strategy has returned 2.48% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26224.409919904236
0.38 0.54 0.7 10 20 70
This st

0.38 0.54 0.85 10 20 70
This strategy has returned 2.25% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26071.784922353556
0.38 0.54 0.85 10 30 60
This strategy has returned 2.17% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26019.259557067908
0.38 0.54 0.85 20 5 85
This strategy has returned 2.23% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26159.569030924184
0.38 0.54 0.85 20 10 70
This strategy has returned 2.16% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26112.93029565192
0.38 0.54 0.85 20 20 60
This strategy has returned 2.09% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26064.074186392278
0.38 0.54 0.85 20 30 50
This strategy has returned 2.02% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26019.551868477472
0.38 0.54 0.85 25 10 6

0.38 0.58 0.65 25 10 65
This strategy has returned 2.26% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26182.43066307804
0.38 0.58 0.65 25 20 55
This strategy has returned 2.16% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26113.575334657056
0.38 0.58 0.7 1 1 98
This strategy has returned 2.82% over 661 trades
Winners: 222, Losers: 439
Winrate: 0.3358547655068079
Sum of all wins: 24150.143433365756
0.38 0.58 0.7 5 10 85
This strategy has returned 2.6% over 661 trades
Winners: 239, Losers: 422
Winrate: 0.3615733736762481
Sum of all wins: 25705.243307828587
0.38 0.58 0.7 10 10 80
This strategy has returned 2.49% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26234.89181546625
0.38 0.58 0.7 10 20 70
This strategy has returned 2.38% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26157.370350667603
0.38 0.58 0.7 10 30 60
This st

0.38 0.58 0.85 10 30 60
This strategy has returned 2.17% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26023.370530616645
0.38 0.58 0.85 20 5 85
This strategy has returned 2.25% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26169.910775875476
0.38 0.58 0.85 20 10 70
This strategy has returned 2.17% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26121.85229622508
0.38 0.58 0.85 20 20 60
This strategy has returned 2.09% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26070.325280225392
0.38 0.58 0.85 20 30 50
This strategy has returned 2.02% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26023.14850259652
0.38 0.58 0.85 25 10 65
This strategy has returned 2.09% over 661 trades
Winners: 246, Losers: 415
Winrate: 0.3721633888048411
Sum of all wins: 26064.987333551795
0.38 0.58 0.85 25 20 55


In [624]:
# Build a dataset to review each trade's metrics
cols = ["tp1", "tp2", "tp3", "p1", "p2", "p3"]
res_dfa = pd.DataFrame(list_of_combos, columns=cols)
res_dfa["winrate"]=winrates
res_dfa["return"]=pct_returns
res_dfa["win_val"]=sum_wins
res_dfa["win_gain"]= res_dfa["win_val"]/(((256+405)*res_dfa["winrate"])*100)

In [626]:
res_dfa#.isna().sum()

tp1   tp2  tp3  p1  p2  p3   winrate  return       win_val  win_gain
0     0.20  0.40  0.6   1   1  98  0.366112    2.64  26031.671803  1.075689
1     0.20  0.40  0.6   5  10  85  0.426626    2.45  29897.780942  1.060205
2     0.20  0.40  0.6  10  10  80  0.476551    2.35  33131.905461  1.051807
3     0.20  0.40  0.6  10  20  70  0.476551    2.24  33059.201852  1.049498
4     0.20  0.40  0.6  10  30  60  0.476551    2.14  32990.125339  1.047306
...    ...   ...  ...  ..  ..  ..       ...     ...           ...       ...
4615  0.38  0.58  0.9  20  10  70  0.372163    2.08  26063.826396  1.059505
4616  0.38  0.58  0.9  20  20  60  0.372163    2.02  26021.175722  1.057771
4617  0.38  0.58  0.9  20  30  50  0.372163    1.96  25982.268031  1.056190
4618  0.38  0.58  0.9  25  10  65  0.372163    2.01  26011.868981  1.057393
4619  0.38  0.58  0.9  25  20  55  0.372163    1.95  25972.761235  1.055803

[4620 rows x 10 columns]

In [629]:
print(f"{256+405} trades")

661 trades


In [687]:
res_dfa[res_dfa["return"]>2.99]

tp1   tp2  tp3  p1  p2  p3   winrate  return       win_val  win_gain
3927  0.36  0.50  0.6   1   1  98  0.340393    3.01  24581.237834  1.092499
4004  0.36  0.54  0.6   1   1  98  0.335855    3.00  24273.305170  1.093392
4081  0.36  0.58  0.6   1   1  98  0.332829    3.03  24088.606109  1.094937
4158  0.38  0.40  0.6   1   1  98  0.366112    3.02  26279.318667  1.085922
4235  0.38  0.44  0.6   1   1  98  0.354009    3.01  25478.515444  1.088825
4312  0.38  0.48  0.6   1   1  98  0.349470    3.04  25194.792025  1.090684
4389  0.38  0.50  0.6   1   1  98  0.343419    3.06  24809.389295  1.092925
4466  0.38  0.54  0.6   1   1  98  0.338880    3.05  24501.573270  1.093820
4543  0.38  0.58  0.6   1   1  98  0.335855    3.07  24316.990469  1.095360

#### SUMMARY OF REVA HYPERPARAMETER TUNE

From our results it is evident that our set of tp/p parameters are not finding the sweet spot for the best trade. The best overall returns come when our tp1 is the highest and the tp3 is lowest with all (98pct) profits being taken at the tp3. So now we need to rebuild our parameter set to take this into account. It's noteworthy that our winrate is low for the best performing trades... this suggests our model is preferring maximising large wins at the expense of overall winrate!!

![alt text](HPrev1_Summary.png "Rev1")

In [ ]:
tp

In [697]:
tp1s = [0.38,0.38,0.38,0.38,0.42,0.42,0.42,0.42,0.46,0.46,0.46,0.46]
tp2s = [0.58,0.62,0.64,0.68,0.62,0.66,0.70,0.72,0.65,0.7,0.74,0.78]
tp3s = [0.60,0.65,0.68,0.72,0.65,0.72,0.75,0.78,0.72,0.78,0.8,0.84] 

p1s = [1, 5, 5, 10]
p2s = [1, 5, 10, 10]
p3s = [98, 90, 85, 80]

In [698]:
list_of_combos = []
winrates = []
pct_returns = []
sum_wins = []
for tp, (tp1, tp2, tp3) in enumerate(zip(tp1s, tp2s, tp3s)):
    for p, (p1, p2, p3) in enumerate(zip(p1s, p2s, p3s)):
        list_of_combos.append([tp1, tp2, tp3, p1, p2, p3])

        # Create a list to store each trade result and some other metrics :))
        results = []
        outcome = []
        max_pct_trade = []

        # List of trade trigger indexes
        trade_idx = trigs.index


        # Now we want to loop through the trade indexes and then back test the trades within the index windows
        for i,j in enumerate(trade_idx[:-1]):
            # Set our triggers to false
            tp1_hit = False
            tp2_hit = False
            tp3_hit = False


            # Set our capital to £100
            capital = 100

            # Set our profit slices give the strategy parameters
            profit_slices = []


            # Query the trade from our supertrend dataset
            trade = df_super.loc[j:trade_idx[i+1]]
            entry_price = trade.iloc[0].close

            # Set a max pct gain tracker for each trade - to be stored in max_pct list
            max_pct_gain = 0

            # Loop through all rows in the isolated trade data
            for index, row in trade.iterrows():
                if row["max_pct"]>max_pct_gain:
                    max_pct_gain=row["max_pct"]


                #print("===========================")
                #print("Trade index: i{} s{}, f{}, Signal direction {}".format(index, 
#                                                                               trade.index[0], 
#                                                                               trade.index[-1], 
#                                                                               trade.signal.iloc[0]))


                # First we calculate the stops and losses

                # If we are on the last candle of the trade and we haven't hit any tps - we have a loser
                # The nature of the data is that the supertrend reversal / stop is hit on the last candle

                if index == trade.index[-1] and tp1_hit==False:

                    #### CALCULATE STOP LOSS VALUE AND APEND TO PROFIT SLICE LIST

                    ## The stop loss value will be the close price minus the entry price below supertrend for buys
                    ## The last index is actually the reversal signal so a buy value means we want to calc our sell stop
                    if row["signal"]=="sell":
                        # Calculate the stop value of our rekt buy trade and add it to the profit list
                        pct_loss = row["close"]/entry_price
                        final_position = pct_loss*100
                        profit_slices.append(final_position)
                        #print("buy loss {}".format(final_position))


                    elif row["signal"]=="buy":
                        # Calculate the stop value of our rekt sell trade and add it to the profit list
                        pct_loss = entry_price/row["close"]
                        final_position = pct_loss*100
                        profit_slices.append(final_position)
                        #print("sell loss {}".format(final_position))

                ## Now what if one or more of our tps have been hit we need to collect the remaining position at stop
                ## First we need to get the percentage price(pp) change from the entry to the supertrend stop
                ## Then we need to take the latest position... take off the tp1/tp2 pct and then take of the pp
                ## Then append this new final position to the profit slices list

                elif index == trade.index[-1] and tp2_hit == True and tp3 == False:
                    # BUYS ... remember buys have a sell signal on the last row signalling reversal
                    if row["signal"]=="sell":

                        # Calculate buys closing at stop
                        tp2_price = entry_price*(1+(tp2/10))

                        close_price = row["close"]

                        pct_change = close_price/tp2_price

                        final_position = capital*pct_change
                        # Add to profit slice
                        profit_slices.append(final_position)


                    elif row["signal"]=="buy": #sells

                        # Calculate sells closing at stop
                        tp2_price = entry_price*(1-(tp2/10))

                        close_price = row["close"]

                        pct_change = tp2_price/close_price

                        final_position = capital*pct_change
                        #Add to profit slice
                        profit_slices.append(final_position)




                elif index == trade.index[-1] and tp1_hit == True:
                    # BUYS ... remember buys have a sell signal on there last row signalling reversal
                    if row["signal"]=="sell":

                        # Calculate buys closing at stop
                        tp1_price = entry_price*(1+(tp1/10))

                        close_price = row["close"]

                        pct_change = close_price/tp1_price

                        final_position = capital*pct_change
                        # Add to profit slice
                        profit_slices.append(final_position)


                    elif row["signal"]=="buy":

                        # Calculate sells closing at stop
                        tp1_price = entry_price*(1-(tp1/10))

                        close_price = row["close"]

                        pct_change = tp1_price/close_price

                        final_position = capital*pct_change
                        #Add to profit slice
                        profit_slices.append(final_position)





                # Now we'll calc the tp winners

                # We need to start with an if statement per tp... elifs will break the strategy as a 
                # single candle could pass thro' tp1 to tp2 and we would not bank relevant profits at tp1!

                if row["max_pct"]>=tp1 and tp1_hit==False:
                    #print(row["max_pct"], tp1)
                    tp1_hit=True
                    position = capital*(1+(tp1/10))
                    profit_take = position*(p1/100)
                    #print("profit take {}".format(profit_take))
                    profit_slices.append(profit_take)
                    # new_position = position*((100-p1)/100)
                    new_position = position-profit_take
                    #print("new position {}".format(new_position))
                    capital = new_position

                if row["max_pct"]>=tp2 and tp2_hit==False:
                    #print(row["max_pct"], tp2)
                    tp2_hit=True
                    position = capital*(1+(tp2/10))
                    profit_take = position*(p2/100)
                    profit_slices.append(profit_take)
                    # new_position = position*((1-p2)/10)
                    new_position = position-profit_take
                    capital = new_position

                if row["max_pct"]>=tp3 and tp3_hit==False:
                    tp3_hit=True
                    position = capital*(1+(tp3/10))
                    profit_take = position*(p3/100)
                    profit_slices.append(profit_take)
                    # new_position = position*((1-p3)/10)
                    new_position = position-profit_take
                    capital = new_position

                #print(tp1_hit, tp2_hit, tp3_hit)


            if tp1_hit==True:
                outcome.append("win")
            else:
                outcome.append("loss")
            max_pct_trade.append(max_pct_gain)
            # Append the sum of our profit list to the trade results list
            #print(profit_slices)
            results.append(sum(profit_slices))


        # Produce report of these trade parameters and add to summary metrics:
        returns = sum(results)
        break_even = 100*len(results)
        gain = returns-break_even
        pct_gain = returns/break_even

        num_wins = len([x for x in results if x>100])
        num_losers = len([x for x in results if x<100])

        winrate = num_wins/len(results)
        pct_return = round(pct_gain*100-100,2)
        winrates.append(winrate)
        pct_returns.append(pct_return)
        wins = [x for x in results if x>100]
        sum_wins.append(sum(wins))
        print("==================================================")
        print(tp1, tp2, tp3, p1, p2, p3)
        print("This strategy has returned {}% over {} trades".format(pct_return, len(results)))
        print("Winners: {}, Losers: {}".format(num_wins, num_losers))
        print("Winrate: {}".format(winrate))
        print("Sum of all wins: {}".format(sum(wins)))
# print("At 10x leverage this is {}%!!".format(round(pct_gain*100-100,2)*10))

0.38 0.58 0.6 1 1 98
This strategy has returned 3.07% over 661 trades
Winners: 222, Losers: 439
Winrate: 0.3358547655068079
Sum of all wins: 24316.99046856018
0.38 0.58 0.6 5 5 90
This strategy has returned 2.89% over 661 trades
Winners: 239, Losers: 422
Winrate: 0.3615733736762481
Sum of all wins: 25895.409883099434
0.38 0.58 0.6 5 10 85
This strategy has returned 2.8% over 661 trades
Winners: 239, Losers: 422
Winrate: 0.3615733736762481
Sum of all wins: 25838.75053628558
0.38 0.58 0.6 10 10 80
This strategy has returned 2.68% over 661 trades
Winners: 245, Losers: 416
Winrate: 0.37065052950075644
Sum of all wins: 26356.9840478777
0.38 0.62 0.65 1 1 98
This strategy has returned 2.92% over 661 trades
Winners: 221, Losers: 440
Winrate: 0.33434190620272314
Sum of all wins: 24119.20677649797
0.38 0.62 0.65 5 5 90
This strategy has returned 2.75% over 661 trades
Winners: 238, Losers: 423
Winrate: 0.3600605143721634
Sum of all wins: 25706.666205443566
0.38 0.62 0.65 5 10 85
This strategy ha

0.46 0.7 0.78 10 10 80
This strategy has returned 2.37% over 661 trades
Winners: 234, Losers: 427
Winrate: 0.3540090771558245
Sum of all wins: 25055.095749444845
0.46 0.74 0.8 1 1 98
This strategy has returned 2.7% over 661 trades
Winners: 216, Losers: 445
Winrate: 0.3267776096822995
Sum of all wins: 23473.53646327961
0.46 0.74 0.8 5 5 90
This strategy has returned 2.55% over 661 trades
Winners: 231, Losers: 430
Winrate: 0.3494704992435703
Sum of all wins: 24872.330872894865
0.46 0.74 0.8 5 10 85
This strategy has returned 2.48% over 661 trades
Winners: 231, Losers: 430
Winrate: 0.3494704992435703
Sum of all wins: 24823.732227531447
0.46 0.74 0.8 10 10 80
This strategy has returned 2.38% over 661 trades
Winners: 234, Losers: 427
Winrate: 0.3540090771558245
Sum of all wins: 25057.48813197488
0.46 0.78 0.84 1 1 98
This strategy has returned 2.61% over 661 trades
Winners: 215, Losers: 446
Winrate: 0.32526475037821484
Sum of all wins: 23314.22855056668
0.46 0.78 0.84 5 5 90
This strategy h

In [699]:
# Build a dataset to review each trade's metrics
cols = ["tp1", "tp2", "tp3", "p1", "p2", "p3"]
res_dfb = pd.DataFrame(list_of_combos, columns=cols)
res_dfb["winrate"]=winrates
res_dfb["return"]=pct_returns
res_dfb["win_val"]=sum_wins
res_dfb["win_gain"]= res_dfb["win_val"]/(((256+405)*res_dfb["winrate"])*100)

In [706]:
res_dfb.sort_values(by="return", ascending=False).head(8)

tp1   tp2   tp3  p1  p2  p3   winrate  return       win_val  win_gain
0   0.38  0.58  0.60   1   1  98  0.335855    3.07  24316.990469  1.095360
16  0.42  0.62  0.65   1   1  98  0.334342    3.00  24169.547834  1.093645
32  0.46  0.65  0.72   1   1  98  0.329803    2.93  23827.310697  1.092996
4   0.38  0.62  0.65   1   1  98  0.334342    2.92  24119.206776  1.091367
1   0.38  0.58  0.60   5   5  90  0.361573    2.89  25895.409883  1.083490
20  0.42  0.66  0.72   1   1  98  0.329803    2.87  23788.237916  1.091204
17  0.42  0.62  0.65   5   5  90  0.355522    2.82  25452.258369  1.083075
2   0.38  0.58  0.60   5  10  85  0.361573    2.80  25838.750536  1.081119

In [703]:
res_dfb[res_dfb["return"]>3]

tp1   tp2  tp3  p1  p2  p3   winrate  return       win_val  win_gain
0  0.38  0.58  0.6   1   1  98  0.335855    3.07  24316.990469   1.09536

#### Run best performer

In [630]:
tp1=0.38
tp2=0.54
tp3=0.6
p1=1
p2=1
p3=98
        
# Create a list to store each trade result and some other metrics :))
results = []
outcome = []
max_pct_trade = []

# List of trade trigger indexes
trade_idx = trigs.index


# Now we want to loop through the trade indexes and then back test the trades within the index windows
for i,j in enumerate(trade_idx[:-1]):
    # Set our triggers to false
    tp1_hit = False
    tp2_hit = False
    tp3_hit = False


    # Set our capital to £100
    capital = 100

    # Set our profit slices give the strategy parameters
    profit_slices = []


    # Query the trade from our supertrend dataset
    trade = df_super.loc[j:trade_idx[i+1]]
    entry_price = trade.iloc[0].close
    
    # Set a max pct gain tracker for each trade - to be stored in max_pct list
    max_pct_gain = 0

    # Loop through all rows in the isolated trade data
    for index, row in trade.iterrows():
        if row["max_pct"]>max_pct_gain:
            max_pct_gain=row["max_pct"]
        
        
        print("===========================")
        print("Trade index: i{} s{}, f{}, Signal direction {}".format(index, 
                                                                      trade.index[0], 
                                                                      trade.index[-1], 
                                                                      trade.signal.iloc[0]))
        

        # First we calculate the stops and losses

        # If we are on the last candle of the trade and we haven't hit any tps - we have a loser
        # The nature of the data is that the supertrend reversal / stop is hit on the last candle

        if index == trade.index[-1] and tp1_hit==False:

            #### CALCULATE STOP LOSS VALUE AND APEND TO PROFIT SLICE LIST

            ## The stop loss value will be the close price minus the entry price below supertrend for buys
            ## The last index is actually the reversal signal so a buy value means we want to calc our sell stop
            if row["signal"]=="sell":
                # Calculate the stop value of our rekt buy trade and add it to the profit list
                pct_loss = row["close"]/entry_price
                final_position = pct_loss*100
                profit_slices.append(final_position)
                print("buy loss {}".format(final_position))


            elif row["signal"]=="buy":
                # Calculate the stop value of our rekt sell trade and add it to the profit list
                pct_loss = entry_price/row["close"]
                final_position = pct_loss*100
                profit_slices.append(final_position)
                print("sell loss {}".format(final_position))
                
        ## Now what if one or more of our tps have been hit we need to collect the remaining position at stop
        ## First we need to get the percentage price(pp) change from the entry to the supertrend stop
        ## Then we need to take the latest position... take off the tp1/tp2 pct and then take of the pp
        ## Then append this new final position to the profit slices list
        
        elif index == trade.index[-1] and tp2_hit == True and tp3 == False:
            # BUYS ... remember buys have a sell signal on the last row signalling reversal
            if row["signal"]=="sell":
                
                # Calculate buys closing at stop
                tp2_price = entry_price*(1+(tp2/10))
                
                close_price = row["close"]
                
                pct_change = close_price/tp2_price
                
                final_position = capital*pct_change
                # Add to profit slice
                profit_slices.append(final_position)
                
            
            elif row["signal"]=="buy": #sells
                
                # Calculate sells closing at stop
                tp2_price = entry_price*(1-(tp2/10))
                
                close_price = row["close"]
                
                pct_change = tp2_price/close_price
                
                final_position = capital*pct_change
                #Add to profit slice
                profit_slices.append(final_position)
        
            
                    
        
        elif index == trade.index[-1] and tp1_hit == True:
            # BUYS ... remember buys have a sell signal on there last row signalling reversal
            if row["signal"]=="sell":
                
                # Calculate buys closing at stop
                tp1_price = entry_price*(1+(tp1/10))
                
                close_price = row["close"]
                
                pct_change = close_price/tp1_price
                
                final_position = capital*pct_change
                # Add to profit slice
                profit_slices.append(final_position)
                
                
            elif row["signal"]=="buy":
                
                # Calculate sells closing at stop
                tp1_price = entry_price*(1-(tp1/10))
                
                close_price = row["close"]
                
                pct_change = tp1_price/close_price
                
                final_position = capital*pct_change
                #Add to profit slice
                profit_slices.append(final_position)
                
            
                


        # Now we'll calc the tp winners

        # We need to start with an if statement per tp... elifs will break the strategy as a 
        # single candle could pass thro' tp1 to tp2 and we would not bank relevant profits at tp1!

        if row["max_pct"]>=tp1 and tp1_hit==False:
            print(row["max_pct"], tp1)
            tp1_hit=True
            position = capital*(1+(tp1/10))
            profit_take = position*(p1/100)
            print("profit take {}".format(profit_take))
            profit_slices.append(profit_take)
            # new_position = position*((100-p1)/100)
            new_position = position-profit_take
            print("new position {}".format(new_position))
            capital = new_position

        if row["max_pct"]>=tp2 and tp2_hit==False:
            print(row["max_pct"], tp2)
            tp2_hit=True
            position = capital*(1+(tp2/10))
            profit_take = position*(p2/100)
            profit_slices.append(profit_take)
            # new_position = position*((1-p2)/10)
            new_position = position-profit_take
            capital = new_position

        if row["max_pct"]>=tp3 and tp3_hit==False:
            tp3_hit=True
            position = capital*(1+(tp3/10))
            profit_take = position*(p3/100)
            profit_slices.append(profit_take)
            # new_position = position*((1-p3)/10)
            new_position = position-profit_take
            capital = new_position
            
        print(tp1_hit, tp2_hit, tp3_hit)
            
    
    if tp1_hit==True:
        outcome.append("win")
    else:
        outcome.append("loss")
    max_pct_trade.append(max_pct_gain)
    # Append the sum of our profit list to the trade results list
    print(profit_slices)
    results.append(sum(profit_slices))


Trade index: i9 s9, f16, Signal direction sell
False False False
Trade index: i10 s9, f16, Signal direction sell
False False False
Trade index: i11 s9, f16, Signal direction sell
False False False
Trade index: i12 s9, f16, Signal direction sell
False False False
Trade index: i13 s9, f16, Signal direction sell
0.402 0.38
profit take 1.038
new position 102.762
True False False
Trade index: i14 s9, f16, Signal direction sell
True False False
Trade index: i15 s9, f16, Signal direction sell
True False False
Trade index: i16 s9, f16, Signal direction sell
True False False
[1.038, 98.52306043915618]
Trade index: i16 s16, f84, Signal direction buy
False False False
Trade index: i17 s16, f84, Signal direction buy
False False False
Trade index: i18 s16, f84, Signal direction buy
False False False
Trade index: i19 s16, f84, Signal direction buy
False False False
Trade index: i20 s16, f84, Signal direction buy
False False False
Trade index: i21 s16, f84, Signal direction buy
False False False
Trad

Trade index: i332 s311, f335, Signal direction buy
False False False
Trade index: i333 s311, f335, Signal direction buy
False False False
Trade index: i334 s311, f335, Signal direction buy
False False False
Trade index: i335 s311, f335, Signal direction buy
buy loss 99.7141416580561
False False False
[99.7141416580561]
Trade index: i335 s335, f365, Signal direction sell
False False False
Trade index: i336 s335, f365, Signal direction sell
False False False
Trade index: i337 s335, f365, Signal direction sell
False False False
Trade index: i338 s335, f365, Signal direction sell
False False False
Trade index: i339 s335, f365, Signal direction sell
False False False
Trade index: i340 s335, f365, Signal direction sell
False False False
Trade index: i341 s335, f365, Signal direction sell
False False False
Trade index: i342 s335, f365, Signal direction sell
False False False
Trade index: i343 s335, f365, Signal direction sell
False False False
Trade index: i344 s335, f365, Signal direction se

Trade index: i704 s685, f777, Signal direction sell
True False False
Trade index: i705 s685, f777, Signal direction sell
True False False
Trade index: i706 s685, f777, Signal direction sell
True False False
Trade index: i707 s685, f777, Signal direction sell
True False False
Trade index: i708 s685, f777, Signal direction sell
True False False
Trade index: i709 s685, f777, Signal direction sell
True False False
Trade index: i710 s685, f777, Signal direction sell
True False False
Trade index: i711 s685, f777, Signal direction sell
True False False
Trade index: i712 s685, f777, Signal direction sell
True False False
Trade index: i713 s685, f777, Signal direction sell
True False False
Trade index: i714 s685, f777, Signal direction sell
True False False
Trade index: i715 s685, f777, Signal direction sell
True False False
Trade index: i716 s685, f777, Signal direction sell
True False False
Trade index: i717 s685, f777, Signal direction sell
True False False
Trade index: i718 s685, f777, Sign

False False False
Trade index: i1085 s1073, f1095, Signal direction buy
False False False
Trade index: i1086 s1073, f1095, Signal direction buy
False False False
Trade index: i1087 s1073, f1095, Signal direction buy
False False False
Trade index: i1088 s1073, f1095, Signal direction buy
False False False
Trade index: i1089 s1073, f1095, Signal direction buy
False False False
Trade index: i1090 s1073, f1095, Signal direction buy
False False False
Trade index: i1091 s1073, f1095, Signal direction buy
False False False
Trade index: i1092 s1073, f1095, Signal direction buy
False False False
Trade index: i1093 s1073, f1095, Signal direction buy
False False False
Trade index: i1094 s1073, f1095, Signal direction buy
False False False
Trade index: i1095 s1073, f1095, Signal direction buy
buy loss 99.70018305102225
False False False
[99.70018305102225]
Trade index: i1095 s1095, f1132, Signal direction sell
False False False
Trade index: i1096 s1095, f1132, Signal direction sell
False False Fal

Trade index: i1467 s1424, f1567, Signal direction sell
True False False
Trade index: i1468 s1424, f1567, Signal direction sell
True False False
Trade index: i1469 s1424, f1567, Signal direction sell
True False False
Trade index: i1470 s1424, f1567, Signal direction sell
True False False
Trade index: i1471 s1424, f1567, Signal direction sell
True False False
Trade index: i1472 s1424, f1567, Signal direction sell
True False False
Trade index: i1473 s1424, f1567, Signal direction sell
True False False
Trade index: i1474 s1424, f1567, Signal direction sell
True False False
Trade index: i1475 s1424, f1567, Signal direction sell
True False False
Trade index: i1476 s1424, f1567, Signal direction sell
True False False
Trade index: i1477 s1424, f1567, Signal direction sell
True False False
Trade index: i1478 s1424, f1567, Signal direction sell
True False False
Trade index: i1479 s1424, f1567, Signal direction sell
True False False
Trade index: i1480 s1424, f1567, Signal direction sell
True Fals

...

False False False
Trade index: i22021 s21996, f22087, Signal direction sell
False False False
Trade index: i22022 s21996, f22087, Signal direction sell
False False False
Trade index: i22023 s21996, f22087, Signal direction sell
False False False
Trade index: i22024 s21996, f22087, Signal direction sell
False False False
Trade index: i22025 s21996, f22087, Signal direction sell
False False False
Trade index: i22026 s21996, f22087, Signal direction sell
False False False
Trade index: i22027 s21996, f22087, Signal direction sell
False False False
Trade index: i22028 s21996, f22087, Signal direction sell
False False False
Trade index: i22029 s21996, f22087, Signal direction sell
False False False
Trade index: i22030 s21996, f22087, Signal direction sell
False False False
Trade index: i22031 s21996, f22087, Signal direction sell
False False False
Trade index: i22032 s21996, f22087, Signal direction sell
False False False
Trade index: i22033 s21996, f22087, Signal direction sell
False False 

Trade index: i22406 s22368, f22411, Signal direction sell
False False False
Trade index: i22407 s22368, f22411, Signal direction sell
False False False
Trade index: i22408 s22368, f22411, Signal direction sell
False False False
Trade index: i22409 s22368, f22411, Signal direction sell
False False False
Trade index: i22410 s22368, f22411, Signal direction sell
False False False
Trade index: i22411 s22368, f22411, Signal direction sell
sell loss 99.89186036291913
False False False
[99.89186036291913]
Trade index: i22411 s22411, f22424, Signal direction buy
False False False
Trade index: i22412 s22411, f22424, Signal direction buy
False False False
Trade index: i22413 s22411, f22424, Signal direction buy
False False False
Trade index: i22414 s22411, f22424, Signal direction buy
False False False
Trade index: i22415 s22411, f22424, Signal direction buy
False False False
Trade index: i22416 s22411, f22424, Signal direction buy
False False False
Trade index: i22417 s22411, f22424, Signal dir

False False False
Trade index: i22884 s22872, f22892, Signal direction sell
False False False
Trade index: i22885 s22872, f22892, Signal direction sell
False False False
Trade index: i22886 s22872, f22892, Signal direction sell
False False False
Trade index: i22887 s22872, f22892, Signal direction sell
False False False
Trade index: i22888 s22872, f22892, Signal direction sell
False False False
Trade index: i22889 s22872, f22892, Signal direction sell
False False False
Trade index: i22890 s22872, f22892, Signal direction sell
False False False
Trade index: i22891 s22872, f22892, Signal direction sell
False False False
Trade index: i22892 s22872, f22892, Signal direction sell
sell loss 99.60818749399996
False False False
[99.60818749399996]
Trade index: i22892 s22892, f22899, Signal direction buy
False False False
Trade index: i22893 s22892, f22899, Signal direction buy
False False False
Trade index: i22894 s22892, f22899, Signal direction buy
False False False
Trade index: i22895 s2289

False False False
Trade index: i23268 s23261, f23271, Signal direction sell
False False False
Trade index: i23269 s23261, f23271, Signal direction sell
False False False
Trade index: i23270 s23261, f23271, Signal direction sell
False False False
Trade index: i23271 s23261, f23271, Signal direction sell
sell loss 99.84976835596757
False False False
[99.84976835596757]
Trade index: i23271 s23271, f23296, Signal direction buy
False False False
Trade index: i23272 s23271, f23296, Signal direction buy
False False False
Trade index: i23273 s23271, f23296, Signal direction buy
False False False
Trade index: i23274 s23271, f23296, Signal direction buy
False False False
Trade index: i23275 s23271, f23296, Signal direction buy
False False False
Trade index: i23276 s23271, f23296, Signal direction buy
False False False
Trade index: i23277 s23271, f23296, Signal direction buy
False False False
Trade index: i23278 s23271, f23296, Signal direction buy
False False False
Trade index: i23279 s23271, f2

Trade index: i23647 s23642, f23656, Signal direction buy
False False False
Trade index: i23648 s23642, f23656, Signal direction buy
False False False
Trade index: i23649 s23642, f23656, Signal direction buy
False False False
Trade index: i23650 s23642, f23656, Signal direction buy
False False False
Trade index: i23651 s23642, f23656, Signal direction buy
False False False
Trade index: i23652 s23642, f23656, Signal direction buy
False False False
Trade index: i23653 s23642, f23656, Signal direction buy
False False False
Trade index: i23654 s23642, f23656, Signal direction buy
False False False
Trade index: i23655 s23642, f23656, Signal direction buy
False False False
Trade index: i23656 s23642, f23656, Signal direction buy
buy loss 99.8219774850024
False False False
[99.8219774850024]
Trade index: i23656 s23656, f23682, Signal direction sell
False False False
Trade index: i23657 s23656, f23682, Signal direction sell
False False False
Trade index: i23658 s23656, f23682, Signal direction 

In [631]:
# 
returns = sum(results)
break_even = 100*len(results)
gain = returns-break_even
pct_gain = returns/break_even
gain, pct_gain

num_wins = len([x for x in results if x>100])
num_losers = len([x for x in results if x<100])

print("This strategy has returned {}% over {} trades".format(round(pct_gain*100-100,2), len(results)))
print("Winners: {}, Losers: {}".format(num_wins, num_losers))
print("Winrate: {}".format(num_wins/len(results)))
# print("At 10x leverage this is {}%!!".format(round(pct_gain*100-100,2)*10))

This strategy has returned 3.05% over 661 trades
Winners: 224, Losers: 437
Winrate: 0.3388804841149773


In [632]:
winout = pd.DataFrame({"result":results, "outcome":outcome, 'maxpct':max_pct_trade})
winout.head()

result outcome  maxpct
0   99.561060     win   0.402
1  115.712319     win   1.343
2   99.821487     win   0.408
3   99.743303    loss   0.082
4   99.524593    loss   0.003

In [584]:
wins = [x for x in results if x>100]
be = len(wins)*100
ret = sum(wins)
be, ret

(27400, 28858.558713711078)

In [586]:
wins

[100.25796726413219,
 109.87190219490569,
 100.46852791945346,
 109.96654445813988,
 110.0451789583464,
 105.05859134590058,
 100.63677573911039,
 109.8061535858358,
 100.51057637799818,
 109.70078129630323,
 100.33296645591119,
 100.43994032368252,
 100.43664363681614,
 109.73911412665235,
 109.68651383492029,
 109.83502988531978,
 104.94876687846767,
 110.14750009014764,
 110.17349583977756,
 104.99042356788343,
 109.76180679048946,
 104.92939652330276,
 109.84881611845547,
 109.7811424772182,
 100.51948790417984,
 105.06443409770503,
 109.69068686942038,
 109.96524864015721,
 104.88562208512298,
 109.69124022759812,
 100.52585487640994,
 109.94095501686557,
 109.762957245342,
 109.76429636685481,
 109.82166950112175,
 110.94187718774937,
 111.05042847009443,
 109.97318250840712,
 110.30577818200447,
 104.85199732673564,
 104.99010706092307,
 105.02919882726702,
 109.7085467491572,
 109.53964910351425,
 109.89357183413293,
 109.699492392422,
 110.01524511563184,
 110.72884953990162,


In [591]:
winout.loc[10:16]

result outcome  maxpct
10   99.801309    loss   0.061
11  110.045179     win   1.722
12   99.804182    loss   0.137
13   99.710572    loss   0.174
14   99.738546    loss   0.220
15  105.058591     win   0.626
16  100.636776     win   0.409

In [676]:
#gt100 = winout[(winout.outcome=="win")]
gt100 = winout[(winout.result>100)]
gt100

result outcome  maxpct
1    115.712319     win   1.343
7    115.718971     win   2.217
11   115.724497     win   1.722
15   115.703584     win   0.626
16   100.029581     win   0.409
..          ...     ...     ...
647  100.048176    loss   0.358
655  100.053944    loss   0.345
656  100.095472     win   0.406
658  115.700239     win   0.745
660  100.012269     win   0.453

[224 rows x 3 columns]

In [672]:
missed_tps = winout[winout.maxpct>tp3]
missed_tps

result outcome  maxpct
1    115.712319     win   1.343
7    115.718971     win   2.217
11   115.724497     win   1.722
15   115.703584     win   0.626
20   115.706502     win   0.846
..          ...     ...     ...
634  115.705196     win   0.683
636  115.706090     win   1.327
637  115.716938     win   1.025
641  115.706905     win   0.621
658  115.700239     win   0.745

[128 rows x 3 columns]

In [682]:
# What is the average missed tp
missed_tps.maxpct.mean()

1.174671875

In [677]:
tp1_wins = gt100.result.sum()
tp1_wins

24501.573270175482

In [680]:
beven = 100*gt100.shape[0]
beven

22400

In [681]:
# Pct gain
tp1_wins/beven

1.0938202352756912

In [636]:
winout[(winout.maxpct>0.88) & (winout.maxpct<1.02)]

result outcome  maxpct
68   115.703468     win   0.907
69   115.704757     win   0.943
70   115.707591     win   0.924
97   115.688969     win   0.941
119  115.704463     win   0.921
122  115.703997     win   0.961
185  115.705435     win   0.982
239  115.713490     win   0.914
266  115.702626     win   0.979
282  115.704468     win   0.979
301  115.713263     win   0.963
309  115.710739     win   0.887
339  115.710598     win   0.953
357  115.713996     win   0.911
368  115.702797     win   0.943
447  115.707733     win   0.915
567  115.705259     win   0.906
597  115.707783     win   0.932
632  115.701475     win   0.955

In [587]:
trigs

time      open      high       low     close  \
9     2022-03-14 00:09:00  37723.24  37725.89  37699.00  37712.00   
16    2022-03-14 00:16:00  37750.61  37846.00  37750.61  37839.84   
84    2022-03-14 01:24:00  38080.27  38094.26  38037.45  38059.44   
116   2022-03-14 01:56:00  38075.68  38087.78  38069.85  38087.78   
122   2022-03-14 02:02:00  38047.23  38066.65  37990.01  37990.01   
...                   ...       ...       ...       ...       ...   
23784 2022-03-30 12:24:00  47223.71  47256.39  47206.89  47256.39   
23831 2022-03-30 13:11:00  47304.82  47304.82  47225.00  47225.07   
23897 2022-03-30 14:17:00  47086.40  47143.32  47052.80  47143.32   
23939 2022-03-30 14:59:00  47163.02  47163.16  47125.45  47137.85   
23978 2022-03-30 15:38:00  47035.97  47084.88  47031.35  47082.02   

            uptrend     downtrend signal  trigger  close_pl  max_pl  max_pct  
9               NaN  37839.792000   sell  sellsig       0.0     0.0      0.0  
16     37616.556977           NaN    buy   buysig       0.0     0.0      0.0  
84              NaN  38218.679324   sell  sellsig       0.0     0.0      0.0  
116    37974.284582           NaN    buy   buysig       0.0     0.0      0.0  
122             NaN  38152.364011   sell  sellsig       0.0     0.0      0.0  
...             ...           ...    ...      ...       ...     ...      ...  
23784  47157.410925           NaN    buy   buysig       0.0     0.0      0.0  
23831           NaN  47320.919457   sell  sellsig       0.0     0.0      0.0  
23897  46909.763691           NaN    buy   buysig       0.0     0.0      0.0  
23939           NaN  47244.443287   sell  sellsig       0.0     0.0      0.0  
23978  46933.599027           NaN    buy   buysig       0.0     0.0      0.0  

[662 rows x 12 columns]

In [590]:
idx1 = 0
idx2 = 1

df_super.loc[trigs.index[idx1]:trigs.index[idx2]]

time      open      high       low     close       uptrend  \
9  2022-03-14 00:09:00  37723.24  37725.89  37699.00  37712.00           NaN   
10 2022-03-14 00:10:00  37712.00  37727.13  37703.99  37721.57           NaN   
11 2022-03-14 00:11:00  37721.57  37725.00  37700.00  37719.75           NaN   
12 2022-03-14 00:12:00  37719.59  37724.30  37680.11  37680.11           NaN   
13 2022-03-14 00:13:00  37683.86  37688.56  37560.40  37630.91           NaN   
14 2022-03-14 00:14:00  37633.93  37644.22  37590.82  37633.30           NaN   
15 2022-03-14 00:15:00  37636.32  37755.30  37627.89  37750.62           NaN   
16 2022-03-14 00:16:00  37750.61  37846.00  37750.61  37839.84  37616.556977   

       downtrend signal  trigger  close_pl  max_pl  max_pct  
9   37839.792000   sell  sellsig      0.00    0.00    0.000  
10  37837.114300   sell    nosig     -9.57    8.01    0.021  
11  37829.398870   sell    nosig     -7.75   12.00    0.032  
12  37820.670983   sell    nosig     31.89   31.89    0.085  
13  37769.547385   sell    nosig     81.09  151.60    0.402  
14  37764.100646   sell    nosig     78.70  121.18    0.321  
15  37764.100646   sell    nosig    -38.62   84.11    0.223  
16           NaN    buy   buysig      0.00    0.00    0.000

## Sandpit

In [46]:
19745/60/24/7

1.9588293650793651

#### BUGS

1. If the trade is on the last candle and we still haven't hit any tps the algo assumes the tps won't be hit in the last candle. The algo assumes the last candle will be a loss making candle in all instances!! We estimate this will affect less than 1% of all trades so not an urgent fix required. I've actually seen this happen. 

In [518]:
df_super

time      open      high       low     close  \
0     2022-03-14 00:00:00  37793.40  37797.17  37763.47  37780.14   
1     2022-03-14 00:01:00  37780.13  37806.22  37757.05  37806.22   
2     2022-03-14 00:02:00  37811.02  37819.97  37794.89  37816.18   
3     2022-03-14 00:03:00  37816.18  37818.51  37756.99  37797.80   
4     2022-03-14 00:04:00  37798.49  37822.67  37786.75  37809.06   
...                   ...       ...       ...       ...       ...   
19740 2022-03-27 17:00:00  44972.54  44994.58  44930.88  44937.04   
19741 2022-03-27 17:01:00  44931.50  44940.00  44900.00  44901.13   
19742 2022-03-27 17:02:00  44902.88  44925.05  44888.83  44898.02   
19743 2022-03-27 17:03:00  44897.65  44921.16  44893.56  44919.29   
19744 2022-03-27 17:04:00  44913.19  44921.22  44912.42  44917.85   

            uptrend  downtrend     signal trigger  close_pl  max_pl  max_pct  
0               NaN        0.0  no_signal     NaN       NaN     NaN      NaN  
1               NaN        NaN  no_signal   nosig       NaN     NaN      NaN  
2               NaN        NaN  no_signal   nosig       NaN     NaN      NaN  
3               NaN        NaN  no_signal   nosig       NaN     NaN      NaN  
4               NaN        NaN  no_signal   nosig       NaN     NaN      NaN  
...             ...        ...        ...     ...       ...     ...      ...  
19740  44824.360025        NaN        buy   nosig    -41.31   16.23    0.036  
19741  44824.360025        NaN        buy   nosig    -77.22  -38.35   -0.085  
19742  44824.360025        NaN        buy   nosig    -80.33  -53.30   -0.119  
19743  44824.360025        NaN        buy   nosig    -59.06  -57.19   -0.127  
19744  44824.360025        NaN        buy   nosig    -60.50  -57.13   -0.127  

[19745 rows x 12 columns]